# Introduction

The Acrobot is a well studied control problem consisting of a double pendulum suspended at a point and actuated at the middle joint only. The goal of the Acrobot controller is to drive the system up into the unstable equilibrium configuration from the hanging rest configuration.

This problem is interesting because it has a simple description but it can be solved in a variety of different ways. More precisely, there are Acrobot specific strategies like the energy-based swing-up <cite data-cite="xin07">[Xin \& Kaneda, 2007]</cite>, as well as general approaches like trajectory optimization or reinforcement learning. Our goal is to use this example problem to learn about various control techniques and how they compare against each other.

## Contents
We will develop solution to this problem in the following sequence:

 1. Build a simple 2D multi-link Acrobot model.
 2. Implement the energy-based swing-up strategy <cite data-cite="xin07">[Xin \& Kaneda, 2007]</cite>.
 3. Implement an optimization based balance strategy.
 4. Employ the value iteration method to solve this problem.
 5. Compare the results.


## Preliminaries
First lets add 8 worker threads to the current Julia kernel for multithreading.

In [1]:
addprocs(8);

We also need to import the necessary Julia visualization and optimization libraries.

In [262]:
using Iterators
using ProgressMeter # Utility for displaying progress (only used for building animations)
@everywhere using StaticArrays # Small fixed sized arrays for an extra performance boost
using Optim # Optimization library with gradient descent, LBFGS, and Newton optimization algorithms.
using Plots
using JLD # For reading and writing Julia data
gr() # Set plots backend;

The macro `@everywhere` above runs the command that follows on all processes we added. This means that the `StaticArrays` module will be available for *all* workers.
We will use the plotting library `Plots.jl` to visualize our pendulum using the following routines:

In [274]:
# Given an array of orientation vectors, for each link starting from the anchor centered at (0,0),
# generate the plot data needed to draw the pendulum. The function `orient` will be defined later.
function plot_data(rs)
    x = Float64[]
    y = Float64[]
    d = [0,0] # origin
    push!(x, d[1])
    push!(y, d[2])
    for r in rs
        d = d - 2*r
        push!(x, d[1])
        push!(y, d[2])
    end
    x, y
end;

# Draw a single frame for the pendulum in the given configuration
function draw(frame, time_data, state, sim, trace)
    rs = orient(sim.acrobot, state)
    w = sim.acrobot.width
    
    link_idx = 1:length(rs) # indices corresponding to each link
    offset = length(link_idx)*2

    # Draw the pendulum links as a plot.
    x,y = plot_data(rs)
    radius = 2*sum(norm.(rs))
    pendulum_plot = begin
        plot_lims = (-radius - 0.1, radius + 0.1)
        plot(x,y,xlims=plot_lims, ylims=plot_lims, color=:orange, w=246*w/radius, label="")
    end
        
    joint_size = 150*w/radius
    
    # Add unactuated joints to pendulum plot
    begin
        scatter!(pendulum_plot, x, y, markercolor=:white, markersize=joint_size, label="")
        cm = center_of_mass(sim.acrobot, state)
    end
    
    # Plot center of mass for each link
    #cms = link_cms(rs)
    #scatter!(pendulum_plot, [cms[1][1], cms[2][1]], [cms[1][2], cms[2][2]], label="")
    
    # Plot the center of mass for the whole acrobot
    #scatter!(pendulum_plot, [cm[1]], [cm[2]], label="")

    # Plot the torque at the active joint
    begin
        τ₁ = time_data[frame,offset+1]
        τ₂ = time_data[frame,offset+2]
        color₁ = τ₁ < 0 ? :blue : :red
        color₂ = τ₂ < 0 ? :blue : :red

        scatter!(pendulum_plot, [x[1]], [y[1]], markercolor=color₁, markeralpha=0.1*abs(τ₁),
                 markersize=joint_size, label="")
        scatter!(pendulum_plot, [x[2]], [y[2]], markercolor=color₂, markeralpha=0.1*abs(τ₂),
                 markersize=joint_size, label="")
    end
    
    # Time dependent plot data
    rng = 1:frame
    t = sim.Δt*[rng-1]
    
    # Draw the trace of the pendulum
    if trace
        trace_x = time_data[rng,offset+4]
        trace_y = time_data[rng,offset+5]
        plot!(pendulum_plot, trace_x, trace_y, label="", color=:lightblue)
    end
    
    # Plot the data on the right-hand-side plots
    xlims = (0, sim.Δt*size(time_data,1))
    
    θ_plots = [plot(t, time_data[rng,i], xlims=xlims, ylims = (-π,π), label="", ylabel="theta_$i")
               for i in link_idx]
    ω_plots = [plot(t, time_data[rng,i + length(link_idx)],
                    xlims=xlims, ylims=(-10,10), label="", ylabel="omega_$i") for i in link_idx]
    state_plots = begin
        if length(link_idx) == 1
            plot(θ_plots[1], ω_plots[1], layout=2)
        elseif length(link_idx) == 2
            plot(θ_plots[1], θ_plots[2], ω_plots[1], ω_plots[2], layout=4)
        end
    end

    τ_plots = begin
        τ₁_plot = plot(t, time_data[rng,offset+1], xlims=xlims, ylims=(-10,10), label="", ylabel="Torque_1")
        if length(link_idx) == 2
            τ₂_plot = plot(t, time_data[rng,offset+2], xlims=xlims, ylims=(-10,10), label="", ylabel="Torque_2")
            plot(τ₁_plot, τ₂_plot, layout=2)
        else
            τ₁_plot
        end
    end
    
    nτ_plots = length(link_idx)
    
    energy_plot = plot(t, time_data[rng,offset + 1 + nτ_plots], xlims=xlims,
        color=:blue, label="Potential", ylabel="Energy", legend=:topleft, bglegend=RGBA(1.0,1.0,1.0,0.5))
    
    plot!(energy_plot, t, time_data[rng,offset + 2 + nτ_plots],
        color=:red, label="Kinetic", legend=:topleft)
    
    rhs_plots = plot(energy_plot, τ_plots, state_plots, layout=(3,1))
    all_plots = plot(pendulum_plot, rhs_plots, layout=2, size=(900,450))
end

# Function for creating an embedded video given a filename
function html_video(filename)
    open(filename) do f
        base64_video = base64encode(f)
        """<video controls src="data:video/x-m4v;base64,$base64_video">"""
    end
end

function show_video(name)
    display("text/html", html_video(name * ".mp4"))
end

function is_valid(val) # check if value is reasonable (not too large, not NaN)
    !isnan(val) && isfinite(val) && abs(val) < 1e20
end;

The following function is used to display the progress of an optimization.

In [191]:
function print_progress(residual, first_residual)
    percent = Int(round(100*(-log10(residual) + log10(first_residual))/(5 + log10(first_residual))))
    blocks = div(percent,2)
    IJulia.clear_output(true)
    print(STDOUT, "Progress: ")
    for prog_i in 1:blocks
       print(STDOUT, "=")
    end
    print(STDOUT, "> $percent%; residual = $residual   ")
end;

# 2D Multi-link Acrobot Model

Below we will implement a simple multi-link pendulum. Recall that the Acrobot with zero applied torque is simply a multi-link pendulum. To start, we will define a few data structures that will store properties and data we will need for simulating the Acrobot. 

Lets parametrize the definition of the Acrobot on the number of links, `N`. Our implementation will support acrobots of 1 or 2 links, where a 1 link Acrobot is a fully actuated system used for testing and debugging.

In [192]:
# Struct defining the intrinsic properties of an Acrobot with any number of links
@everywhere struct Acrobot{N}
    masses::SVector{N,Float64} # Each link may have a different mass
    lengths::SVector{N,Float64} # Each link may have a differnt length
    width::Float64 # All links have the same width
    
    # A flexible constructor initializes all masses and lengths to 1.0 by default.
    function Acrobot{N}(;masses=ones(SVector{N,Float64}), lengths=ones(SVector{N,Float64}), width=0.1) where N
        new(masses,lengths,width)
    end
end;

We will not track the explicit positions of the pendulum links, but instead we will track the orientations $\theta = (\theta_1, \theta_2)$ and the angular velocities $\omega = (\omega_1, \omega_2)$ of each link. This means that the state of the entire two link pendulum can be described in 4D:

$$ 
    s = (\theta_1, \theta_2, \omega_1, \omega_2)\ \in\ [-\pi,\pi)^2 \times \mathbb{R}^2\ \subset\ \mathbb{R}^4.
$$

This state can be encapsulated into a structure as follows:

In [193]:
@everywhere struct State{N}
    θ::SVector{N,Float64} # Counter-clockwise angle from the downward direction
    ω::SVector{N,Float64} # Angular velocity
    
    # State constructor.
    function State{N}(θ=zeros(SVector{N,Float64}), ω=zeros(SVector{N,Float64})) where N
        new(θ,ω)
    end
end

We will also need to refer to the physical properties of the pendulum for simulation. For each link $i$, we will need the mass matrix and moment of inertia defined as
\begin{align*}
    M_i &= \begin{pmatrix} m_i & 0 \\ 0 & m_i \end{pmatrix} \\
    I_i &= \frac{m_i}{12} (l_i^2 + w^2)
\end{align*}
respectively, where $m_i$ is the mass, $l_i$ is the length of link $i$; $w$ is the width which is fixed for all links. We will also need to store the frictional damping coefficient $k_d$ and the gravitational acceleration constant $g = 9.81 \mathrm{m/s^2}$

In [194]:
# Physical properties of the acrobot. These are used in the simulation
@everywhere struct Properties{N}
    kd::Float64 # frictional damping coefficient
    g::Float64 # gravitational acceleration (absolute value)
    Ms::SVector{N,SMatrix{2,2,Float64}} # Mass matrix for each link
    Is::SVector{N,Float64} # Moment of inertia for each link

    # Constructor
    function Properties{N}(acrobot::Acrobot{N}, kd, g) where N
        Id2 = eye(SMatrix{2,2,Float64})
        Ms = [m*Id2 for m in acrobot.masses]   # mass matrix
        w = acrobot.width
        Is = [(m/12) * (l*l + w*w) for (m,l) in zip(acrobot.masses, acrobot.lengths)] # inertia
        new(kd, g, Ms, Is)
    end
end

Now consider a 2D one-link pendulum system with no friction, attached to a ceiling and subject to the gravitational force. The Newton equations of motion balance the net force on the pendulum with the change in its momentum:
\begin{align*}
F + F_g = m \ddot{p}
\end{align*}
where $F$ is the constraint force of the hinge on the ceiling and $F_g$ is the force of gravity. As usual, $m$ is the mass of the pendulum and $p$ is the 2D position of its centre of mass. We can rewrite these as:
\begin{align}
m \ddot{p} - F = mg \tag{1}
\end{align}
where $F_g = mg$, and $g$ is the gravitational acceleration constant. Here, the right-hand-side corresponds to known external forces applied to the system, while the left-hand-side collects the unknowns.

Let $\theta$ represent the tilt of the pendulum where $\theta = 0$ corresponds to the stable equilibrium configuration. Then let $\omega = \dot{\theta}$ the angular velocity of the pendulum about its centre of mass. We can now write the angular equations of motions relating the relevant rotational quantities as follows:
\begin{align*}
\tau &= \frac{DL}{Dt} = \dot{L} \\
r_xF_{y} - r_yF_{x} &= I\dot{\omega}
\end{align*}
where $I$ is the moment of inertia making up angular momentum $L = I\omega$. In 2D, the torque, $\tau$, generated by the constraint is expressed in terms of the constraint force as $r_xF_{y} - r_yF_{x}$, where $r = (r_x, r_y)$ is the vector from the centre of the pendulum to the point of contact at the hinge, and $F = (F_x, F_y)$. As before, collecting unknowns on the left-hand-side gives us 
\begin{align*}
I\dot{\omega} - r_xF_{y} + r_yF_{x} = 0 \tag{*}
\end{align*}
For brevity, we denote $\tilde{r} = (r_y, -r_x)$, simplifying (*) to
\begin{align}
I\dot{\omega} + \tilde{r} \cdot F = 0 \tag{2} 
\end{align}


Finally, the hinge constraint ensures that the acceleration of the pendulum, $\ddot{p_r}$, at the hinge is zero:
\begin{align*}
0 &= \ddot{p_r} = \ddot{p} -  \dot{\omega}\tilde{r} - \omega^2r.
\end{align*}
Rearranging terms as before gives us:
\begin{align}
- \ddot{p} + \dot{\omega}\tilde{r} = -\omega^2r \tag{3} 
\end{align}

Putting equations (1), (2) and (3) together, we get the following system (omitting the zeros in the matrix):
\begin{align*}
\begin{pmatrix}
m\mathbb{1} &   & -\mathbb{1} \\
  & I & \tilde{r} \\
-\mathbb{1} & \tilde{r}^{\top} &  \\
\end{pmatrix}
\begin{pmatrix}
\ddot{p}^{\top} \\ \dot{\omega} \\ F^{\top}
\end{pmatrix}
 =
\begin{pmatrix}
mg^{\top} \\ 0 \\ -\omega^2r^{\top}
\end{pmatrix},
\end{align*}
where $\mathbb{1}$ is the 2x2 identity matrix, and the superscript ${}^{\top}$ converts a vector into a column vector. Solving for $(\ddot{p}, \dot{\omega}, F)$ gives us the linear and angular accelerations, which we can use to update the pendulum configuration by one time step. We will only need $\dot{\omega}$ to update the pendulum but the other quantities can be useful in developing other actuation strategies and visualization.

We can extend this model easily to handle multiple links since each consecutive link is a hinge constraint on the previous. In addition, the Acrobot allows non-zero torques applied to the second hinge, which manifests as a torque included in the right-hand-side of equation (2). The following represents a fully actuated two-link system:
\begin{align*}
\begin{pmatrix}
m_1\mathbb{1} &   & -\mathbb{1} & & &\mathbb{1} \\
  & I_1 & \tilde{r}_1 & & & -\tilde{r}_2 \\
-\mathbb{1} & \tilde{r}_1^{\top} &  & & & \\
& & & m_2\mathbb{1} &   & -\mathbb{1} \\
& & &   & I_2 & \tilde{r}_2 \\
\mathbb{1} & -\tilde{r}_2^{\top} & & -\mathbb{1} & \tilde{r}_2^{\top} &  \\
\end{pmatrix}
\begin{pmatrix}
\ddot{p}_1^{\top} \\ \dot{\omega}_1 \\ F^{\top}_1 \\
\ddot{p}_2^{\top} \\ \dot{\omega}_2 \\ F^{\top}_2
\end{pmatrix}
 =
\begin{pmatrix}
m_1g^{\top} \\ \tau_1 \\ -\omega_1^2r^{\top}_1 \\
m_2g^{\top} \\ \tau_2 \\ -\omega_2^2r^{\top}_2
\end{pmatrix},
\end{align*}
where $\tau_1$ and $\tau_2$ are torques applied to the first and second hinges. By definition, $\tau_1 = 0$ for the Acrobot. The system with $\tau_2 = 0$ (only the first hinge is actuated) is called a Pendubot.

Note that our model doesn't involve $(\theta_1, \theta_2)$ directly, so we need a function to convert $(\theta_1,\theta_2)$ into the vector $r$ by rotating each link from the equilibrium configuration by angle $\theta_i$ as follows
$$
    r_i = \begin{pmatrix} \cos\theta_i & -\sin\theta_i \\ \sin\theta_i & \cos\theta_i \end{pmatrix} \begin{pmatrix} 0 \\ l_i/2 \\ \end{pmatrix}.
$$
The following function implements this operation efficiently:

In [195]:
# Produce the vectors from the center of mass of each link to its anchor.
@everywhere function orient(acrobot::Acrobot{N}, state::State{N}) where N
    r = zeros(MVector{N,SVector{2,Float64}})
    for i in 1:N
        r[i] = SVector(-sin(state.θ[i]), cos(state.θ[i])) * 0.5*acrobot.lengths[i] # acrobot configuration
    end
    SVector(r)
end;

Finally lets define the simulation structure, which encapsulates an `Acrobot` and its `Properties`. We can also use this structure to store the system solved during simulation as described above.

In [196]:
@everywhere mutable struct Simulation{N}
    acrobot::Acrobot{N}
    properties::Properties{N}
    Δt::Float64 # time step
    
    # Dynamics System
    A::Matrix{Float64}
    b::Vector{Float64}
    
    # Constructor
    function Simulation{N}(acrobot::Acrobot{N}; Δt=0.02, kd=0.05, g=9.81) where N
        # initialize properties
        properties = Properties{N}(acrobot, kd, g)
        
        # initialize the dynamics system
        A = zeros(Float64, N*5,N*5)
        b = zeros(Float64, N*5)
        
        state = State{N}()
        rs = orient(acrobot, state) # zero state
        skew(r) = SVector(r[2], -r[1]) 

        # Block diagonal parts
        for off in 0:N-1
            i = off+1
            r = rs[i]
            r̃ = skew(r)
            ω = state.ω[i]
            idx = (1:5) + 5*off
            M, I = properties.Ms[i], properties.Is[i]
            m, g, kd = acrobot.masses[i], properties.g, properties.kd
            A[idx,idx] =
                [M       [0;0]  -eye(2);
                 [0 0]   I      r̃';
                 -eye(2) r̃      zeros(2,2)]
            b[idx] = [m*[0.0, -g]; -kd*ω; -ω*ω*r]
        end

        # Coupling parts
        for off in 1:N-1
            r = -rs[off]
            r̃ = skew(r)
            ω = state.ω[off]
            i = (4:5) + 5*off
            j = (1:3) + 5*(off - 1)
            A[i,j] = [eye(2)  -r̃]
            A[j,i] = A[i,j]' # symmetry
            b[i] += ω*ω*r
        end
        
        new(acrobot, properties, Δt, A, b)
    end
end

We will use the `advance` function to update the given Acrobot configuration forward by $\Delta t$ in time by solving the constrained dynamics system we described above.

The parameter $\tau = (\tau_1, \tau_2)$ is the torque applied to each hinge. Note that in the results later presented, $\tau_1 = 0$ unless explicitly specified otherwise.

The `advance` function is broken into two steps. First we update the system stored in our `Simulation` data structure using the function `update`, then we solve the resulting system, and return the new state. The input state remains unchanged.

In [197]:
# Update the simulation matrix and solve the resulting system.
@everywhere function update(state::State{N}, sim::Simulation{N}, τ::SVector{N,Float64}) where N
    skew(r) = SVector(r[2], -r[1]) # utility function to apply the 2D Levi-Civita symbol.
    
    rs = orient(sim.acrobot, state)
    
    # Update block diagonal parts
    for off in 0:N-1
        i = off+1
        r = rs[i]
        r̃ = skew(r)
        ω = state.ω[i]
        rows = (4:5) + 5*off
        col = 3 + 5*off
        sim.A[rows,col] = r̃
        sim.A[col,rows] = r̃'
        sim.b[(3:5) + 5*off] = [-sim.properties.kd*ω; -ω*ω*r]
        sim.b[col] += τ[i] # Apply actuator torque
    end

    # Update Coupling parts
    for off in 1:N-1
        r = -rs[off]
        r̃ = skew(r)
        ω = state.ω[off]
        i = (4:5) + 5*off
        j = 3 + 5*(off - 1)
        sim.A[i,j] = -r̃
        sim.A[j,i] = -r̃' # symmetry
        sim.b[i] += ω*ω*r
    end

end

# Advance the given state forward in time by sim.Δt
@everywhere function advance(state::State{N}, sim::Simulation{N}, τ::SVector{N,Float64}) where N
    update(state, sim, τ) # update system
    
    x = sim.A\sim.b # solve system

    θ′ = zeros(MVector{N,Float64})
    ω′ = zeros(MVector{N,Float64})
    # Update configuration
    for i in 1:N
        ω′[i] = state.ω[i] + x[3 + 5*(i-1)]*sim.Δt
        θ′tmp = state.θ[i] + ω′[i]*sim.Δt
        θ′[i] = θ′tmp + (θ′tmp <= 0 ? 2*π : (θ′tmp > 2*π ? -2*π : 0.0)) # normalize angles
    end
    
    State{N}(θ′, ω′)
end;

The following routine will simulate the acrobot for some number of frames and record the results in a plot using the function `draw` as defined above. The consecutive generated plots for each frame will be saved as an MPEG video file.

In [232]:
# The following routine animates the pendulum given an iterator of configurations
function anim(init_state::State{N},
              sim::Simulation{N},
              torque,
              advance,
              name,
              frames,
              trace=false,
              force_resim=false) where N
    if force_resim || !isfile(name * ".mp4")
        state = init_state
        # time series
        offset = N*2
        time_data = zeros(Float64, frames, offset + N + 4)
        progress = Progress(frames)
        animation = @animate for i=1:frames
            θs_disp = [θ > π ? θ-2*π : θ for θ in state.θ]
            time_data[i, 1:N] = θs_disp
            time_data[i, N + (1:N)] = state.ω

            τ = torque(state) # input torque is a function of state
            Ep = potential_energy(sim.acrobot, state, sim.properties)
            Ek = kinetic_energy(sim.acrobot, state, sim.properties)
            time_data[i, offset + (1:N+2)] = [τ' Ep Ek]
            x,y = plot_data(orient(sim.acrobot, state))
            time_data[i, offset + 2 + N + (1:2)] = [x[end], y[end]]
            draw(i, time_data, state, sim, trace)
            state = advance(state, sim, τ)
            next!(progress)
            if any([!is_valid(val) for val in [state.θ' state.ω' τ']])
                println(STDERR, "\nFound invalid values: ", [state.θ' state.ω' τ'])
                break
            end
        end
        mp4(animation, "./" * name * ".mp4", fps = Int(1.0/sim.Δt))
    end
    show_video(name)
end;

It is also useful to compute the center of mass and energy of our 2 link pendulum for visualization and designing actuation policies as we will see later. Since we parametrized the Acrobot by the number of links, we can simply implement each function for the specific type of Acrobot separately. For instance
```julia
function center_of_mass(acrobot::Acrobot{1}, state::State{1}) ... end
```
defines the center of mass for the one-link pendulum, while
```julia
function center_of_mass(acrobot::Acrobot{2}, state::State{2}) ... end
```
defines it for the two-link pendulum.

In [273]:
# Compute center of mass for each link
@everywhere function link_cms(rs::SVector{1,SVector{2,Float64}})
    SVector{1,SVector{2,Float64}}(-rs[1])
end
@everywhere function link_cms(rs::SVector{2,SVector{2,Float64}})
    SVector{2,SVector{2,Float64}}(-rs[1], -2*rs[1] - rs[2])
end

# Compute the center of mass of the Acrobot as a whole
@everywhere function center_of_mass(acrobot::Acrobot{1}, state::State{1})
    link_cms(orient(acrobot, state))[1]
end
@everywhere function center_of_mass(acrobot::Acrobot{2}, state::State{2})
    cms = link_cms(orient(acrobot, state))
    0.5*(cms[1] + cms[2])
end

@everywhere function potential_energy(acrobot::Acrobot{1}, state::State{1}, properties::Properties{1})
    cms = link_cms(orient(acrobot, state))
    g = properties.g
    ms = acrobot.masses
    ls = acrobot.lengths
    
    # potential energy is zero in stable equillibrium
    g*(sum([m*cm[2] for (cm,m) in zip(cms,ms)]) + ms[1]*ls[1]) 
end
@everywhere function potential_energy(acrobot::Acrobot{2}, state::State{2}, properties::Properties{2})
    cms = link_cms(orient(acrobot, state))
    g = properties.g
    ms = acrobot.masses
    ls = acrobot.lengths
    g*(sum([m*cm[2] for (cm,m) in zip(cms,ms)]) + ms[1]*ls[1])  + g*ms[2]*(ls[2]+2*ls[1])
end

@everywhere function kinetic_energy(acrobot::Acrobot{1}, state::State{1}, properties::Properties{1})
    I, m, l = properties.Is[1], acrobot.masses[1], acrobot.lengths[1]
    ω = state.ω[1]
    0.5*(I + m*l*l/4)*ω*ω
end

@everywhere function kinetic_energy(acrobot::Acrobot{2}, state::State{2}, properties::Properties{2})
    I, m, l = properties.Is, acrobot.masses, acrobot.lengths
    ω = state.ω
    r = orient(acrobot, state)

    0.5*(I[1] + m[1]*l[1]*l[1]/4)*ω[1]*ω[1] +
    0.5*(I[2] + m[2]*l[2]*l[2]/4)*ω[2]*ω[2] +
    0.5*m[1]*(l[1]*l[1]*ω[1]*ω[1] + 4*dot(r[2],r[1])*ω[1]*ω[2]) # coupling    
end

In [200]:
# The following utility functions will help us deal with periodic state space of angles
@everywhere function θ_diff(θ₁::SVector{N,Float64}, θ₂::SVector{N,Float64}) where N
    map(θ₁ - θ₂) do d
        d < 0.0 ? d + 2π : d
    end
end
@everywhere function θ_dist(θ₁::SVector{N,Float64}, θ₂::SVector{N,Float64}) where N
    norm(min.(θ_diff(θ₁, θ₂), θ_diff(θ₂, θ₁))) # shortest distance between two angles.
end

For convenience we will define some interesting initial configurations we will use in our examples. In each we opt to have zero initial angular velocity:

In [201]:
# Stable equilibrium
function init_stable(::Type{Val{N}}) where N
    θs = SVector{N,Float64}(collect(Iterators.take([2π, 2π], N))) # initial angles
    State{N}(θs, zeros(SVector{N,Float64}))
end

# The pendulum in its unstable equilibrium configuration.
function init_unstable(::Type{Val{N}}) where N
    θs = SVector{N,Float64}(collect(Iterators.take([π, π], N))) # initial angles
    State{N}(θs, zeros(SVector{N,Float64}))
end

# The pendulum perturbed slightly from the unstable equilibrium configuration.
function init_vertical_perturbed(::Type{Val{N}}) where N
    θs = SVector{N,Float64}(collect(Iterators.take([π+0.1, π-0.2], N))) # initial angles
    State{N}(θs, zeros(SVector{N,Float64}))
end

# Both links aligned with the horizontal.
function init_horizontal(::Type{Val{N}}) where N
    θs = SVector{N,Float64}(collect(Iterators.take([π/2, π/2], N))) # initial angles
    State{N}(θs, zeros(SVector{N,Float64}))
end

# Both links at 45 degrees from the horizontal.
function init_diagonal(::Type{Val{N}}) where N
    θs = SVector{N,Float64}(collect(Iterators.take([3*π/4, 3*π/4], N))) # initial angles
    State{N}(θs, zeros(SVector{N,Float64}))
end;

## First Examples

Lets instantiate a standard Acrobot that we will use in the rest of our examples. The `masses` and `lengths` will be initialized to `1.0` and the width to `0.1` as defined by the default arguments to the Acrobot constructor:

In [202]:
const ACROBOT = Acrobot{2}();

To verify that our definitions work, we can run a few assertions on the functions we defined above.

In [203]:
@assert center_of_mass(ACROBOT, init_unstable(Val{2}))[2] == 1.0
@assert kinetic_energy(ACROBOT, init_horizontal(Val{2}), Simulation{2}(ACROBOT).properties) == 0.0
@assert begin
    state′ = advance(init_stable(Val{2}), Simulation{2}(ACROBOT), zeros(SVector{2}))
    norm(state′.ω - init_stable(Val{2}).ω) < 1e-9 &&
    θ_dist(state′.θ, init_stable(Val{2}).θ) == 0.0
end

To allow the Julia compiler to optimize as much as possible, we will avoid defining mutable data in the global scope, and instead opt to encapsulate as much as possible in functions. Lets start by timing the simulation of a two-link pendulum. This test can be used to benchmark performance of the `advance` function:

In [204]:
function test_simulation(frames)
    sim = Simulation{2}(ACROBOT)
    res = State{2}[]
    state = init_diagonal(Val{2})
    for i in 1:frames
        push!(res, state)
        state = advance(state, sim, SVector(0.0,0.0))
    end
    state
end;

In [205]:
@time test_simulation(10000);

  0.275431 seconds (1.14 M allocations: 51.416 MiB, 9.45% gc time)


Advancing the simulation by 1000 steps will produce animation of a double pendulum swinging back and forth:

In [206]:
function frictionless_pendulum(init_state::State{N}) where N
    sim = Simulation{2}(ACROBOT; Δt=0.02, kd=0.0)
    anim(init_state, sim,
         s -> SVector(0.0,0.0), # No torque applied, a simple two-link pendulum.
         advance,               # Specify the advance function. We can try different simulators here.
         "pendulum_horizontal_test", # Filename of the output video.
         1000, # Number of frames.
         #=trace=# true) # Output the trace of the end of the pendulum to see its chaotic trajectory.
end

frictionless_pendulum(init_diagonal(Val{2}))

To verify that the applied torque generates valid results, we add a constant torque to the middle joint turning the double pendulum into an Acrobot:

In [207]:
function constant_torque_acrobot(init_state::State{N}) where N
    sim = Simulation{2}(ACROBOT; Δt=0.02, kd=0.0)
    anim(init_state, sim,
         s -> SVector(0.0,1.0), # No torque applied, a simple two-link pendulum.
         advance,               # Specify the advance function. We can try different simulators here.
         "acrobot_constant_torque_test", # Filename of the output video.
         500, # Number of frames.
         #=trace=# true) # Output the trace of the end of the pendulum to see its chaotic trajectory.
end
constant_torque_acrobot(init_horizontal(Val{2}))

In the videos above, the Acrobot is drawn in orange with its joints coloured in red if the applied torque is positive (counter clockwise) and blue if it is negative (clockwise).

We now have a concrete forward dynamics model of a 2D two-link Acrobot, which we can use as an input to a learning algorithm for instance. Below we discuss possible solutions to the acrobot swinging and balancing problem.

# Solving the Acrobot Problem

The primary goal of a simple acrobot is to balance itself vertically in its unstable equilibrium using one actuator located between the two links. In other words we need to find the function $\tau(s)$ that gives the ideal torque for each possible state $s$ of our acrobot.

> ### Aside on the Choice of State Space
> It is tempting to assume that for some time $t > 0$ and some initial conditions $s_0$ at time $t = 0$, we can reliably compute $s(t)$ (the state of our system at time $t$) reducing our state space to one dimension (i.e. the solution we would seek is of form $\tau(t)$) but also making the solution dependent on initial conditions. In general (assuming a purely virtual world), computing $s(t)$ is subject to truncation errors of the time integration scheme. If the acrobot was built in the real world, many unforeseen factors may affect the state $s(t)$ that would be difficult to predict with a forward simulation. For these reasons we will first look for a solution as a function of the whole configuration space in order to robustly react to unforeseen configurations. 



## Energy-Based Swing-up Strategy

One approach to achieving our goal is to prescribe an explicit torque strategy to effectively swing the acrobot into its vertical position.
Some successful strategies <cite data-cite="xin02">[Xin \& Kaneda, 2002]</cite>, <cite data-cite="xin07">[Banavar \& Mahindrakar, 2003]</cite> have been proposed and verified numerically to converge to the target upright configuration. Below we implement the control law proposed in <cite data-cite="xin02">[Xin \& Kaneda, 2002]</cite> that swings the acrobot back and forth until it converges to the unstable equilibrium. We confirm the results presented in the paper by reproducing their simulation.

In [208]:
function energy_swingup_demo()
    swing_bot = Acrobot{2}(;lengths=[1.0,2.0])
    sim = Simulation{2}(swing_bot; Δt=0.02, kd=0.0)
    g = sim.properties.g
    
    ms, ls = swing_bot.masses, swing_bot.lengths
    Is = sim.properties.Is
    lc = [l/2 for l in ls];
    t1 = ms[1]*lc[1]*lc[1] + ms[2]*ls[1]*ls[1] + Is[1]
    t2 = ms[2]*lc[2]*lc[2] + Is[2]
    t3 = ms[2]*ls[1]*lc[2]
    t4 = ms[1]*lc[1] + ms[2]*ls[1]
    t5 = ms[2]*lc[2]

    # Energy based swing-up torque
    function energy_swingup(state::State{2})
        kv = 45.0
        ke = 0.5
        kd = 15.0
        kp = 22.0
        q̇ = SVector(state.ω[1], state.ω[2] - state.ω[1])
        q = SVector(state.θ[1] - π/2, state.θ[2] - state.θ[1])

        d11 = t1 + t2 + 2*t3*cos(q[2])
        d12 = t2 + t3*cos(q[2])
        d22 = t2
        D = SMatrix{2,2}(d11, d12, d12, d22)

        h1 = t3*(-2*q̇[1]*q̇[2] - q̇[2]*q̇[2])*sin(q[2])
        h2 = t3*q̇[1]*q̇[1]*sin(q[2])
        C = SVector{2}(h1, h2)

        g1 = t4*g*cos(q[1]) + t5*g*cos(q[1] + q[2])
        g2 = t5*g*cos(q[1] + q[2])
        G = SVector{2}(g1, g2)

        Δ = d11*d22 - d12*d12
        E = 0.5*q̇'*D*q̇ + t4*g*sin(q[1]) + t5*g*sin(q[1] + q[2]) # total energy
        Etop = (t4 + t5)*g # Energy at unstable equillibrium
        Ẽ = E - Etop
        SVector(0.0, (-(kv*q̇[2] + kp*q[2])*Δ - kd*(d12*(h1 + g1) - d11*(h2 + g2)))/(ke*Ẽ*Δ + kd*d11))
    end;
    
    # Alternative 2-link pendulum simulator from
    # "The Swing up Control for the Acrobot based on Energy Control Approach" by Xin and Kaneda
    # This simulator supports only two links and computes only angular acceleration.
    #=function advance(state::State{2}, sim::Simulation{2}, τ::SVector{2,Float64})
        q̇ = [state.ω[1], state.ω[2] - state.ω[1]]
        q = [state.θ[1] - π/2, state.θ[2] - state.θ[1]]

        d11 = t1 + t2 + 2*t3*cos(q[2])
        d12 = t2 + t3*cos(q[2])
        d22 = t2
        D = [d11 d12; d12 d22]

        h1 = t3*(-2*q̇[1]*q̇[2] - q̇[2]*q̇[2])*sin(q[2])
        h2 = t3*q̇[1]*q̇[1]*sin(q[2])
        C = [h1, h2]

        g1 = t4*g*cos(q[1]) + t5*g*cos(q[1] + q[2])
        g2 = t5*g*cos(q[1] + q[2])
        G = [g1, g2]

        b = τ - C - G

        x = D\b

        θ′ = MVector(state.θ)
        ω′ = MVector(state.ω)

        ω′[1] += sim.Δt*x[1]
        ω′[2] += sim.Δt*(x[2] + x[1])
        θ′[1] += sim.Δt*ω′[1]
        θ′[2] += sim.Δt*ω′[2]
        State{2}(θ′, ω′)
    end;=#
    
    anim(init_horizontal(Val{2}), sim, energy_swingup, advance, "energy_swingup_test", 2000)
end;

In [209]:
energy_swingup_demo()

It is clear from the implementation above that the energy-based swing-up law is simply a torque function $\tau(s)$ that depends entirely on the current state of the acrobot, making it especially fast to compute. Although this explicit strategy is very efficient and easy to implement, it doesn't generalize nicely for more complex problems. 

## Balancing

For proper balancing, we need to introduce a toruqe that will push the center of mass of the acrobot to be right above the anchor (which is located at the origin) when it's above the horizontal. Let $p_{cm} (0,2\pi]^2 \to \mathbb{R}^2$ denote the center of mass for the Acrobot:
$$
    p_{cm}(\theta_1,\theta_2) = \frac{l_1}{4}\begin{pmatrix} -\sin\theta_1 \\ \cos\theta_1 \end{pmatrix} +
        \frac{l_2}{4}\begin{pmatrix} -\sin\theta_2 \\ \cos\theta_2 \end{pmatrix}
$$

### Naive Approach

At a first glance it may be tempting to derive the desired torque from a PD control scheme. For instance, we would like to achieve the following acceleration for $p_{cm}$:
$$
    \ddot{p}_{pd} = k_p(p_{r} - p_{cm}) - k_d\dot{p}_{cm}
$$
where $p_r = (0,\frac{l_1+l_2}{2})$ is the target for the center of mass and $k_p$ and $k_d$ are the PD control parameters. Then if we were allowed to actuate both hinges of the Acrobot, we could determine the torques needed to achieve this acceleration:

$$
    \tau = \mathbf{J}^{-1}(\ddot{p}_{pd} - \dot{\mathbf{J}} \omega)
$$
where $\mathbf{J}$ is the Jacobian of $p_{cm}$:
$$
    \mathbf{J} = -\frac{1}{4}\begin{pmatrix} l_1\cos\theta_1 & l_2\cos\theta_2 \\ l_1\sin\theta_1 & l_2\sin\theta_2 \end{pmatrix}.
$$
This will not work for a fully actuated system because $\mathbf{J}$ is often singular (e.g. when $\theta_1 = \theta_2$), which will produce large torques whenever the acrobot is almost straight. For the true Acrobot, we may use the above equations to compute the desired torque $\tau_2$ in terms of the $x$ component of the $p_{cm}$, which does not have this problem. Note that the required torque would also need to counteract the effect of gravity which is not considered above.

The difficulty with this solution is its sensitivity to the chosen time step and figuring out the right coefficients to use for the controller. I have not been able to achieve balance using this method for longer than two second of simulation.

### Optimization Approach

#### Simple

With the same goal in mind, we may opt for optimization. Instead of the guessing what the torque should be, we can explicitly compute the torque required to minimize the distance between the current center of mass of the Acrobot and its desired center of mass. For brevity, let $g[s](\tau) = \mathtt{advance}(s, \mathtt{sim}, \tau)$, for a given simulation `sim`. Then we can minimize the following objective over the torque applied at the second hinge, $\tau$:
$$
    f(s, \tau) = \left\|\left(0,\tfrac{l_1 + l_2}{2}\right) - p_{cm}\left(g[s](\tau)\right)\right\|^2.
$$
This objective penalizes horizontal distance from the target center of mass, which is precisely what we are looking for.

#### With Lookahead

Note that the immediate torque required to push the acrobot towards its unstable equilibrium may not be optimal in the long run. Luckily our formulation allows us to go one step further. Instead of optimizing for the immediate reward, we can optimize for a trajectory into some number of steps into the future. Let $n$ be the number of time steps to look ahead. Then the objective we'd like to minimize over becomes
$$
        f(s, \tau) = \left\|\left(0,\tfrac{l_1 + l_2}{2}\right) - p_{cm}\left(g^n[s](\tau)\right)\right\|^2,
$$
where $g^n[s] = \underbrace{g \circ g \circ \dots \circ g}_{n}[s]$, a composition of $g$ with itself $n$ times. Furthermore, we don't have to recompute this minimization at every step, instead we can find an optimal trajectory and follow it for say $\lfloor n/4 \rfloor$ steps and repeat the process on the $\lfloor n/4 \rfloor + 1$'th step. It is worth noting that since we are looking for small torques, it is better to reset the initial guess for the optimization algorithm to zero.

To perform this optimization we employ the `Optim.jl` Julia package that performs unconstrained optimization (more specifically we use L-BFGS). Although we rely on finite differences for computing gradients of our objective $f$, it is worth noting that better performance and accuracy may be achieved by supplying explicit formulas for the gradient.

In [276]:
function balance_test(init_state::State{N}, filename, lookahead::Int64=30) where N
    # Record precomputed torques here
    torque_buffer = zeros(Float64, lookahead)
    count = lookahead # count invalid torques in the buffer
    τ_limit = 10
    
    # This controller produces a torque on the middle joint that pushes the x component of
    # the center of mass of the acrobot to zero.
    function balance_control(sim::Simulation{2}, s::State{2})
        max_height = mean(sim.acrobot.lengths)
        # If there are not enough torques in the buffer, compute more
        if count > div(lookahead,8) # If more than half of the torques are invalid, recompute
            function f(τs)
                s′ = State{2}(s.θ, s.ω)
                for τ in τs
                    s′ = advance(s′, sim, SVector(0.0, τ))
                end
                cm = center_of_mass(sim.acrobot, s′)
                cm[1]*cm[1] + (cm[2] - max_height)*(cm[2] - max_height)
            end
            
            count = 0 # reset counter

            result = optimize(f, zeros(lookahead), LBFGS(), Optim.Options(iterations = 1000))

            torque_buffer = map(result.minimizer) do τ
                max(-τ_limit, min(τ_limit, τ)) # Clamp torques at the limits.
            end
        end
        
        count += 1
        SVector{2}(0.0, torque_buffer[count])
    end;
    
    sim = Simulation{2}(ACROBOT; Δt=0.02, kd=0.05, g=9.81)
    anim(init_state, sim, s -> balance_control(sim,s), advance, filename, 250)
end;

### Examples

First lets try to apply the "simple" optimization approach of looking ahead one time step to see what happens.

In [211]:
balance_test(init_vertical_perturbed(Val{2}), "acrobot_shallow_balance_test", 1)

It is clear that this method is ineffective and produces spuriously large torques.

Now lets observe what happens when we look ahead for 60 frames.

In [245]:
balance_test(init_vertical_perturbed(Val{2}), "acrobot_full_balance_test_vertical_perturbed11",60)

This is much more stable, although requires substantially more computation to complete. Below are more examples with different configurations

In [213]:
balance_test(State{2}(SVector(π/2-0.01, π/2+0.01), zeros(SVector{2})), "acrobot_full_balance_test_horizontal", 60)

In [214]:
balance_test(init_diagonal(Val{2}), "acrobot_full_balance_test_diagonal", 60)

Although the above examples look promising, this method doesn't work as well when the pendulum center of mass is below the horizontal. Here is an example where the pendulum fails to swing up even with a large lookahead window:

In [284]:
balance_test(State{2}(SVector(0.01, -0.02), zeros(SVector{2})), "acrobot_full_balance_test_stable2",200)

Notice that the torques generated often exceed the limit. It is possible that a larger lookahead window could produce better results, but the this incurs a stiff performance penalty.

## Discussion

Although this method produces good results, it depends on the initial state, and it is not always clear how many steps we need to lookahead and how many do we trust (before we recompute the torques). In the next section we will attempt to find a solution independing of the initial state.

# Reinforcement Learning

To start, lets define the problem in the most general sense as a Markov decision proces (MDP) $(S,A,\{P_{sa}\}, \gamma, R)$:

 * $S = (0,2\pi]^2 \times \mathbb{R}^2\ \subset\ \mathbb{R}^4$ is the set of all possible states of the Acrobot.
 * $A = \{\tau\in\mathbb{R}\ :\ |\tau| < c \}$ is the set of acceptable torques (or actions) that our an Acrobot may apply to the middle joint.
 * $P_{sa} : S \to [0,1]$ is the probability distribution on the state space where $P_{sa}(s^{\prime})$ gives the probability that we land in state $s^{\prime}$ after taking the action (applying a torque) $a$ from state $s$.
 * $\gamma \in [0,1)$ is the discount factor which we can use to penalize the amount of time it takes for the Acrobot to balance itself.
 * $R : S \times A \to \mathbb{R}$ is the reward function. For example, the higher the center of mass of the Acrobot, the closer it is to its unstable equilibrium configuration. In addition we may also reward using low torques if we were to build a real energy efficient Acrobot for instance.

The Markov decision process follows by choosing an initial state $s_0$ and applying actions from $A$, produces a sequences of new states $s_i$:
$$
s_0 \rightarrow s_1 \rightarrow s_2 \rightarrow\,...
$$

Our goal is to find a policy $\mu : S \to A$ that gives actions that produce states with maximal expected sum of discounted rewards:
$$
V^{\mu}(s_0) := E[R(s_0) + \gamma R(s_1) + \gamma^2 R(s_2) + \cdots],
$$

which is called the value function $V : S \to \mathbb{R}$. The value function satisfies the Bellman equations:
$$
V^{\mu}(s) = \sum_{s^{\prime}\in S} P_{s\mu(s)}(s^{\prime})(R(s^{\prime}) + \gamma V^{\mu}(s^{\prime})),
$$
which we can use to compute the value function and the policy itself as
$$
\mu(s) = \arg\min_{a\in A} \sum_{s^{\prime}\in S} P_{sa}(s^{\prime})V^{\mu}(s^{\prime})
$$


## Value iteration
The idea of value iteration is to determine the optimal value function over the finite state space using fixed point iteration on the Bellman expectation backup over this function defined as

$$
V^*(s) = \max_{a\in A}\sum_{s^{\prime}\in S} P_{sa}(s^{\prime})\left(R(s^{\prime}) + \gamma V^*(s^{\prime})\right),
\quad \forall s\in S
$$

This method could be considered appropriate given that our state space is small and discrete.
To discretize our domain, we sample the space of angles $(0,2\pi]$ with $n\theta s$  points and angular velocities $(-\omega\_limit,\omega\_limit]$ with $n\omega s$ points. Further to simplify matters, we allow a discrete set of torques. This automatically limits possible torques, which prevents unrealistic motion.

### Discretization

The following structure contains all information necessary for discretization:

In [216]:
# Discretize the state space using a grid. The same grid would work for any number of links.
@everywhere struct StateGrid
    nθs::Int64 # Number of possible discrete angles (should be even to capture π).
    nωs::Int64 # Number of possible discrete angular velocities (should be odd to capture 0 velocity).
    nτs::Int64 # Number of available torques. (should be odd to capture 0.0). This is the size of our action set.
    ω_limit::Float64 # Maximum allowed angular velocity.
    τ_limit::Float64 # Maximum allowed torque.
    
    # Constructor
    StateGrid(;nθs=6,nωs=7,nτs=9,ω_lim=9.0,τ_lim=9.0) = new(nθs,nωs,nτs,ω_lim,τ_lim)
end

Below we provide functions to index each state. This can also be achieved by storing the states explicitly in arrays.

In [217]:
@everywhere θ(st::StateGrid, i::Int64) = Float64(i*2π/st.nθs) # Convert index to angle.
@everywhere ω(st::StateGrid, i::Int64) = Float64(2*st.ω_limit*((i-1)/(st.nωs - 1) - 0.5)) # ... to angular velocity.
@everywhere τ(st::StateGrid, i::Int64) = 2*st.τ_limit*((i-1)/(st.nτs-1) - 0.5)

@everywhere θ_step(st::StateGrid) = θ(st, 1) # Distance between consecutive θles
@everywhere ω_step(st::StateGrid) = Float64(2*st.ω_limit/(st.nωs-1))  # Distance between consecutive ω samples

Additionally it will be useful to query the nearest grid state provided a state from our continuous space (e.g. after a simulation step):

In [218]:
# Lookup nearest grid value to given angle.
@everywhere iθ(st::StateGrid, θ::Float64) = Int64(round(st.nθs*θ/(2π)))
 # Lookup nearest grid value to given angular velocity.
@everywhere iω(st::StateGrid, ω::Float64) = Int64(round((st.nωs-1)*(0.5+ω/(2*st.ω_limit)))) + 1

To test our discretization we will check identities and all state and torque values:

In [219]:
# Check identities
function test_discretization()
    grid = StateGrid() # default discretization
    @assert iθ(grid, θ(grid, 42)) == 42
    @assert iω(grid, ω(grid, 42)) == 42
    @assert abs(θ(grid, iθ(grid, Float64(pi))) - π) < 1e-9
    @assert ω(grid, iω(grid, 0.0)) == 0.0

    @assert abs(θ(grid, 1) - θ(grid, 2)) == θ_step(grid)
    @assert abs(abs(ω(grid, 1) - ω(grid, 2)) - ω_step(grid)) < 1e-9
    @assert abs(abs(τ(grid, 1) - τ(grid, 2)) - 2*grid.τ_limit/(grid.nτs - 1)) < 1e-9
    
    print("By default, the state space is discretized into a finite number ");
    println("of angles, angular velocities and torques as follows")
    println("θ = ", θ.(grid, 1:grid.nθs))
    println("ω = ", ω.(grid, 1:grid.nωs))
    println("τ = ", τ.(grid, 1:grid.nτs))
end
test_discretization()

By default, the state space is discretized into a finite number of angles, angular velocities and torques as follows
θ = [1.0472, 2.0944, 3.14159, 4.18879, 5.23599, 6.28319]
ω = [-9.0, -6.0, -3.0, 0.0, 3.0, 6.0, 9.0]
τ = [-9.0, -6.75, -4.5, -2.25, 0.0, 2.25, 4.5, 6.75, 9.0]


Now that we have discretized all the variables in our state, we can define functions to access this state from a particular 4D index (2D for one-link Acrobot):

In [220]:
# Function to convert indices to actual states
@everywhere function state_at(grid::StateGrid, idx::SVector{4,Int64})
    State{2}(SVector(θ(grid, idx[1]), θ(grid, idx[3])), SVector(ω(grid, idx[2]), ω(grid, idx[4])))
end
@everywhere function state_at(grid::StateGrid, idx::SVector{2,Int64})
    State{1}(SVector(θ(grid, idx[1])), SVector(ω(grid, idx[2])))
end

The following utility functions map linear indices to a set of 4 (for two-link Acrobot) or 2 (for one-link Acrobot) indices. These will be used in tandem with `state_at` to pick discrete states from a sequence of numbers (with `expand_index#`) and find their neighbouring states (with `expand_offset#`).

In [221]:
# For 2 link acrobot only
@everywhere function expand_index2(grid::StateGrid, idx::Int64) # Convert linear index into state indices
    off = idx - 1
    i = rem(off,grid.nθs) + 1
    off = div(off,grid.nθs)
    j = rem(off,grid.nωs) + 1
    off = div(off,grid.nωs)
    k = rem(off,grid.nθs) + 1
    off = div(off,grid.nθs)
    l = rem(off,grid.nωs) + 1
    SVector(i,j,k,l)
end
# For 1 link acrobot only
@everywhere function expand_index1(grid::StateGrid, idx::Int64) # Convert linear index into state indices
    off = idx - 1
    i = rem(off,grid.nθs) + 1
    off = div(off,grid.nθs)
    j = rem(off,grid.nωs) + 1
    SVector(i,j)
end
# For 2 link acrobot only
@everywhere function expand_offset2(off::Int64) # Convert linear offset into state offsets in [-1,0,1] each
    i = rem(off,3)-1
    off = div(off,3)
    j = rem(off,3)-1
    off = div(off,3)
    k = rem(off,3)-1
    off = div(off,3)
    l = rem(off,3)-1
    SVector(i,j,k,l)
end
# For 1 link acrobot only
@everywhere function expand_offset1(off::Int64) # Convert linear offset into state offsets in [-1,0,1] each
    i = rem(off,3)-1
    off = div(off,3)
    j = rem(off,3)-1
    SVector(i,j)
end

## Reward Function

One of the key ingredients for value iteration is choosing the right reward function. This function controls how the optimal policy will be determined. A number of functions that can be useful in designing a particular reward are provided below, although not all are used in the final results.

In [250]:
# The height of the center of mass of the Acrobot.
@everywhere function height(acrobot::Acrobot{N}, s::State{N}) where N
    center_of_mass(acrobot, s)[2]
end

# Reward in terms of energy (maximize potential energy, minimize kinetic energy)
# The following is the negative of the lagrangian
@everywhere function neg_lagrangian(a::Acrobot{N}, s::State{N}, p::Properties{N}) where N
    potential_energy(a, s, p) - kinetic_energy(a, s, p)
end

# Given angle θ and angular velocity ω, determine what penalties should be applied
# if θ is θ_limit degrees above the horizontal or
# if ω is greater than ω_limit in magnitude
@everywhere function boundary_penalty(θ, θ_limit, θ_penalty, ω, ω_limit, ω_penalty)
    if θ > 3*π/2 - θ_limit || θ < π/2 + θ_limit
        θ_penalty
    elseif abs(ω) > ω_limit
        ω_penalty
    else
        0.0
    end
end

# Reward function for a one-link Acrobot
@everywhere function reward(s::State{1}, sim::Simulation{1}, ω_limit::Float64, bdry_penalty::Float64)
    penalty = boundary_penalty(s.θ[1], π/12, bdry_penalty/4, s.ω[1], ω_limit, bdry_penalty)
    
    θt = θ_dist(s.θ, SVector{1,Float64}(π))
    res = -bdry_penalty - θt*θt - s.ω[1]*s.ω[1]
    res + penalty
end

# Reward function for a two-link Acrobot
@everywhere function reward(s::State{2}, sim::Simulation{2}, ω_limit::Float64, bdry_penalty::Float64)
    penalty = min(boundary_penalty(s.θ[1], π/9, bdry_penalty/2, s.ω[1], ω_limit, bdry_penalty),
                  boundary_penalty(s.θ[2], π/9, bdry_penalty/4, s.ω[2], ω_limit, bdry_penalty))

    cm = center_of_mass(sim.acrobot, s)
    θt = θ_dist(s.θ, SVector{2,Float64}(π, π))
    accept = -bdry_penalty - θt*θt - 40*abs(s.ω[1])
    if cm[2] < 0
       accept += 7*bdry_penalty
    else
        accept += 90*cm[2] - 70*abs(cm[1])
    end

    accept + penalty
end

## Probability Kernel

Since our simulation is deterministic, the probability function is not, strictly speaking, correspond to a probability. It is there merely as an interpolation tool since there is almost no chance that one step of the simulation produces a state that is in our discrete domain. Thus we are free to design an interpolation kernel that suits the problem. In particular, since we are free to chose different discretizations for angles and angular velocities, it makes sense to interpolate these states separately and combine their contributions via multiplication.

Lets define a probability/interpolation kernel to be an approximation to the normal distribution with compact support. In particular we chose
$$
    p_{\sigma}(x) = \left\{\begin{array}{ll}\frac{3}{2\sigma}\left(1-\frac{x}{\sigma}\right)^4\left(4\frac{x}{\sigma} + 1\right),
                &\ \mathrm{ if }\ \sigma < 1 \\
            0&\ \mathrm{ otherwise}
            \end{array}\right.
$$
as our kernel, which integrates to 1, has compact support and approximates the Gaussian.

In [223]:
@everywhere function prob_kernel(x, σ=1.0)
    r = abs(x/σ)
    if r > 1.0
        0.0
    else
        t = (1.0 - r)
        (3/(2*σ))*(t*t*t*t)*(4.0*r + 1.0)
    end
end

To compute the contribution of one state to the value of another, we:
 * evaluate the Euclidean distance between the angles and separately, the angular velocities,
 * evaluate the kernel at each distance separately,
 * multiply the results, and
 * normalize.
 
The normalization step here is not critical since we normalize the results at each computation to handle boundaries (states at boundaries of the discrete domain space will have missing contributions for some neighbours).

In [224]:
@everywhere function state_prob(s_new::State{2}, neigh::State{2}, grid::StateGrid, kernel_scale::Float64)
    d1 = θ_dist(s_new.θ, neigh.θ)
    d2 = norm(s_new.ω - neigh.ω)
    Δθ = θ_step(grid)
    Δω = ω_step(grid)
    r1 = Δθ*kernel_scale # standard deviation
    r2 = Δω*kernel_scale
    (196/(9*π*π*r1*r2))*Δθ*Δθ*Δω*Δω*prob_kernel(d1,r1)*prob_kernel(d2,r2)
end

@everywhere function state_prob(s_new::State{1}, neigh::State{1}, grid::StateGrid, kernel_scale::Float64)
    d1 = θ_dist(s_new.θ, neigh.θ)
    d2 = norm(s_new.ω - neigh.ω)
    r1 = θ_step(grid)*kernel_scale # standard deviation
    r2 = ω_step(grid)*kernel_scale
    θ_step(grid)*ω_step(grid)*prob_kernel(d1,r1)*prob_kernel(d2,r2)
end

Finally we test the claims made above about our interpolation kernels.

In [225]:
function test_prob() # Test probability kernel
    g = StateGrid(;nθs=20,nωs=21,nτs=21)
    Δθ = θ_step(g)
    Δω = ω_step(g)
    
    # simple test
    probs = [0.01*prob_kernel(x) for x in -1:0.01:1]
    println(sum(probs))
    @assert abs(sum(probs) - 1.0) < 1e-3
    
    # Problem specific tests

    # Test that the probability function sums to 1
    probs = begin
        r1 = 3.0
        [(14/(3*π*r1))*Δθ*Δθ*prob_kernel(θ_dist(SVector(θ(g,i), θ(g,j)), SVector(π/4, π/4)),r1)
            for i in 1:g.nθs for j in 1:g.nθs]
    end
    println(sum(probs))
    @assert abs(sum(probs) - 1.0) < 1e-3
    # use heatmap(θ(1:nθs), θ(1:nθs), probs) to visualize

    probs = begin
        r1 = 6.0
        [(14/(3*π*r1))*Δω*Δω*prob_kernel(norm([ω(g,i), ω(g,j)]),r1) for i in 1:g.nωs for j in 1:g.nωs]
    end
    println(sum(probs))
    @assert abs(sum(probs) - 1.0) < 1e-2

    # Combining two probability functions together
    probs = begin
        r1 = 4.0
        r2 = 6.0
        [(14/(3*π*r1))*Δθ*Δθ*prob_kernel(θ_dist(SVector(θ(g,i), θ(g,j)), SVector(1π, 1π)),r1)*
         (14/(3*π*r2))*Δω*Δω*prob_kernel(norm([ω(g,k), ω(g,l)]),r2)
            for i in 1:g.nθs for j in 1:g.nθs for k in 1:g.nωs for l in 1:g.nωs]
    end
    println(sum(probs))
    @assert abs(sum(probs) - 1.0) < 1e-2

    probs = begin
        r1 = 3.0
        [Δθ*prob_kernel(θ_dist(SVector(θ(g,i)), SVector(1π)), r1) for i in 1:g.nθs]
    end
    println(sum(probs))
    @assert abs(sum(probs) - 1.0) < 1e-3

    probs = begin
        r2 = 3.0
        [Δω*prob_kernel(norm([ω(g,i)]), r2) for i in 1:g.nωs]
    end
    println(sum(probs))
    @assert abs(sum(probs) - 1.0) < 1e-2

end
test_prob();

1.000000005
0.9999890879625422
1.0000974414330281
0.998154660646144
1.0000597403734233
1.004148


In [226]:
function test_state_prob() # Test state probability function
    g = StateGrid(;nθs=20,nωs=21,nτs=21)
    probs = [state_prob(State{2}(SVector(π/4, π/4), zeros(SVector{2})), state_at(g, SVector(i,j,k,l)), g, 1.3)
             for i in 1:g.nθs for j in 1:g.nωs for k in 1:g.nθs for l in 1:g.nωs]
    println(sum(probs))
    @assert abs(sum(probs) - 1.0) < 0.01

    probs = [state_prob(State{1}(SVector(π/2), SVector(0.0)), state_at(g, SVector(i,j)), g, 4.0)
             for i in 1:g.nθs for j in 1:g.nωs]
    println(sum(probs))
    @assert abs(sum(probs) - 1.0) < 0.01
end
test_state_prob();

0.9995208198564545
1.0039100646972656


## The Algorithm

Now we are ready to implement the value iteration algorithm. In order to perform the computations in parallel, we need to use two multi-dimensional `SharedArray` structures. This allows for eight worker processes to write data to a central location.

In [283]:
@everywhere mutable struct ValueIteration{D} # D indicates dimensions
    grid::StateGrid
    γ::Float64 # Discount factor
    boundary_penalty::Float64
    kernel_scale::Float64  # Should be less than sqrt(2) to maintain a 3x3(x3x3) interpolation stencil
    V::SharedArray{Float64,D} # Value function, one value for each state
    μ::SharedArray{Float64,D} # policy
    
    function ValueIteration{D}(grid; γ=0.99, bdry_penalty=-80, kernel_scale=1.3) where D
        new(grid, γ, bdry_penalty, kernel_scale)
    end
end
function init(vi::ValueIteration{2})
    vi.V = SharedArray{Float64,2}(vi.grid.nθs, vi.grid.nωs)
    vi.μ = SharedArray{Float64,2}(vi.grid.nθs, vi.grid.nωs)
end
function init(vi::ValueIteration{4})
    vi.V = SharedArray{Float64,4}(vi.grid.nθs, vi.grid.nωs, vi.grid.nθs, vi.grid.nωs)
    vi.μ = SharedArray{Float64,4}(vi.grid.nθs, vi.grid.nωs, vi.grid.nθs, vi.grid.nωs)
end;

We roughly follow the algorithm as it is defined in a variety of sources including [Wikipedia](https://en.wikipedia.org/wiki/Markov_decision_process) and [Reinforcement Learning Lecture Notes from Stanford](http://cs229.stanford.edu/notes/cs229-notes12.pdf).

The function `discrete_vi` below is an implementation of one fixed point iteration. To maintain reasonable performance we only loop through the immediate neighbours of each state after applying a torque.

In [228]:
# Value iterate for two link pendulum
function discrete_vi(vi::ValueIteration{4}, sim::Simulation{2})
    A = τ.(vi.grid, 1:vi.grid.nτs) # action set
    nθs = vi.grid.nθs
    nωs = vi.grid.nωs
    num_states = nθs*nωs*nθs*nωs
    @sync @parallel for idx in 1:num_states
        sidx = expand_index2(vi.grid, idx)
        s = state_at(vi.grid, sidx)
        i,j,k,l = sidx
        vi.V[i,j,k,l], vi.μ[i,j,k,l] = begin
            maxval = -vi.boundary_penalty
            maxtau = 0.0 # initialized action
            for torque in A
                s_new = advance(s, sim, SVector(0.0, torque))
                newval = 0.0
                denom = 0.0
                for off in 0:80
                    near_idx = SVector(iθ(vi.grid, s_new.θ[1]), iω(vi.grid, s_new.ω[1]),
                                       iθ(vi.grid, s_new.θ[2]), iω(vi.grid, s_new.ω[2])) 
                    offset = expand_offset2(off)
                
                    near_idx += offset
                    i2,j2,k2,l2 = near_idx
                    if  i2 < 1 || j2 < 1 || k2 < 1 || l2 < 1 ||
                        i2 > nθs || j2 > nωs || k2 > nθs || l2 > nωs
                        continue
                    end
                    s′ = state_at(vi.grid, near_idx)
                    p = state_prob(s_new, s′, vi.grid, vi.kernel_scale)
                    denom += p
                    newval += p*(reward(s′, sim, vi.grid.ω_limit, vi.boundary_penalty) + vi.γ*vi.V[i2,j2,k2,l2])
                end

                newval /= denom
                if maxval < newval
                    maxval = newval
                    maxtau = torque
                end
            end
            maxval, maxtau
        end
    end
end

# Value iterate for 1 link acrobot
function discrete_vi(vi::ValueIteration{2}, sim::Simulation{1})
    A = τ.(vi.grid, 1:vi.grid.nτs) # action set
    nθs = vi.grid.nθs
    nωs = vi.grid.nωs
    num_states = nθs*nωs
    @sync @parallel for idx in 1:num_states
        sidx = expand_index1(vi.grid, idx)
        s = state_at(vi.grid, sidx)
        i,j = sidx
        vi.V[i,j], vi.μ[i,j] = begin
            maxval = -vi.boundary_penalty
            maxtau = 0.0
            for torque in A
                s_new = advance(s, sim, SVector(torque))
                newval = 0.0
                denom = 0.0

                for off in 0:9
                    near_idx = SVector(iθ(vi.grid, s_new.θ[1]), iω(vi.grid, s_new.ω[1]))
                    offset = expand_offset1(off)
                    
                    near_idx += offset
                    i2,j2 = near_idx
                    if  i2 < 1 || j2 < 1 || i2 > nθs || j2 > nωs
                        continue
                    end
                    
                    s′ = state_at(vi.grid, near_idx)
                    p = state_prob(s_new, s′, vi.grid, vi.kernel_scale)
                    denom += p
                    newval += p*(reward(s′, sim, vi.grid.ω_limit, vi.boundary_penalty) + vi.γ*vi.V[i2,j2])
                end
                
                newval /= denom
                if maxval < newval
                    maxval = newval
                    maxtau = torque
                end
            end
            maxval, maxtau
        end
    end

end;

Finally, define the main loop in `train_vi` that iterates until convergence producing the optimal value function and policy:

In [229]:
# Value iteration for acrobot
function train_vi(vi::ValueIteration{4}, sim::Simulation{2})
    first_residual = -1.0
    residual = 0.0
    num_states = vi.grid.nθs*vi.grid.nωs*vi.grid.nθs*vi.grid.nωs
    
    # Cleanup
    for idx in 1:num_states
        i,j,k,l = expand_index2(vi.grid, idx)
        vi.V[i,j,k,l] = 0.0
        vi.μ[i,j,k,l] = 0.0
    end
    
    # loop until convergence
    while true
        V_old = copy(vi.V)
        discrete_vi(vi,sim)
        residual = norm(vec(vi.V - V_old))
        if (residual < 1e-5)
            break
        end
        if first_residual < 0
            first_residual = residual
        end
        print_progress(residual, first_residual)
    end
    println("\nfinal residual = ", residual)
    vi, sim
end

# Value iteration for one link acrobot
function train_vi(vi::ValueIteration{2}, sim::Simulation{1})
    first_residual = -1.0
    residual = 0.0
    num_states = vi.grid.nθs*vi.grid.nωs

    # Cleanup
    for idx in 1:num_states
        i,j, = expand_index1(vi.grid, idx)
        vi.V[i,j] = 0.0
        vi.μ[i,j] = 0.0
    end
    
    while true
        V_old = copy(vi.V)
        discrete_vi(vi,sim)
        residual = norm(vec(vi.V - V_old))
        if residual < 1e-5
            break
        end
        if first_residual < 0
            first_residual = residual
        end
        print_progress(residual, first_residual)
    end

    println("\nfinal residual = ", residual)
    vi, sim
end;


The function `get_optimal_policy` simply converts the optimal policy into a function over the continuous domain by interpolating with neighbouring grid states:

In [230]:
function get_optimal_policy(vi::ValueIteration{4})
    function policy(s::State{2})
        torque = 0.0
        denom = 0.0
        num_states = vi.grid.nθs*vi.grid.nωs*vi.grid.nθs*vi.grid.nωs
        for idx in 1:num_states
            i,j,k,l = expand_index2(vi.grid, idx)
            neigh = state_at(vi.grid, SVector(i,j,k,l))
            near_torque = vi.μ[i,j,k,l]
            p = state_prob(s, neigh, vi.grid, vi.kernel_scale)
            denom += p
            torque += near_torque*p
        end
        if denom != 0.0
            torque /= denom
        end
        SVector(0.0, torque)
    end
end;
function get_optimal_policy(vi::ValueIteration{2})
    function policy(s::State{1})
        torque = 0.0
        denom = 0.0
        num_states = vi.grid.nθs*vi.grid.nωs
        for idx in 1:num_states
            i,j = expand_index1(vi.grid, idx)
            neigh = state_at(vi.grid, SVector(i,j))
            near_τ = vi.μ[i,j]
            p = state_prob(s, neigh, vi.grid, vi.kernel_scale)
            denom += p
            torque += near_τ*p
        end
        if denom != 0.0
            torque /= denom
        end
        SVector(torque)
    end
end;

## Results

### One-link Acrobot

First lets balance a single link Acrobot:

In [234]:
@time vi1, sim1 = begin
    vi = ValueIteration{2}(StateGrid(;nθs=16,nωs=7,nτs=9,ω_lim=9.0,τ_lim=9.0))
    init(vi)
    one_link_bot = Acrobot{1}()
    sim = Simulation{1}(one_link_bot)
    train_vi(vi, sim);
end;

Progress: ==================================================> 100%; residual = 1.005520170807345e-5   
final residual = 9.953690012743518e-6
 17.534846 seconds (8.06 M allocations: 381.891 MiB, 1.05% gc time)


Let's look at the resulting value function and also print the reward map for reference:

In [282]:
begin # plot value function and find minimum and maximum values
    println("Value function for the 1 link acrobot:")
    flush(STDOUT)
    display(heatmap(ω.(vi1.grid, 1:vi1.grid.nωs), θ.(vi1.grid, 1:vi1.grid.nθs), vi1.V[:,:], aspect_ratio=1))
    println("min value = ", minimum(vi1.V))
    println("max value = ", maximum(vi1.V))
    println("Reward function for the 1 link acrobot:")
    flush(STDOUT)
    num = vi1.grid.nθs*vi1.grid.nωs
    rew(i) = reward(state_at(vi1.grid, expand_index1(vi1.grid, i)), sim1, vi1.grid.ω_limit, vi1.boundary_penalty)
    reward_mtx = reshape([rew(i) for i in 1:num], vi1.grid.nθs, vi1.grid.nωs)
    display(heatmap(ω.(vi1.grid, 1:vi1.grid.nωs), θ.(vi1.grid, 1:vi1.grid.nθs), reward_mtx, aspect_ratio=1))
    println("min reward = ", minimum(reward_mtx))
    println("max reward = ", maximum(reward_mtx))
end

Value function for the 1 link acrobot:


<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 -10 
 
 
 -5 
 
 
 0 
 
 
 5 
 
 
 10 
 
 
 1 
 
 
 2 
 
 
 3 
 
 
 4 
 
 
 5 
 
 
 6 
 
 
<image width="498" height="149" xlink:href="data:;base64,
iVBORw0KGgoAAAANSUhEUgAAAfIAAACVCAYAAACjF3iGAAAFRElEQVR4nO3cu47UdRjGcWb2v0eW
hYVIkFMh4iFQEBMMnY13YOUdeGl2FiYmFtpp4TnRAqRQSBR3AVlYFvY44xUMhc37PsnncwVPMTPf
eZvf6OtbH02PMdPayk71hLbGIx+dWZaXdqsntLW4tFc9gUBPn65VT2hrXD0AAPj/hBwAggk5AAQT
cgAIJuQAEEzIASCYkANAMCEHgGBCDgDBhvXV7eoNra2vb1VPaGs6HVVPaGv35VL1hLa2tk5WT2jr
aOK2mmV7d7l6Qls+NQAQTMgBIJiQA0AwIQeAYEIOAMGEHACCCTkABBNyAAg2rB7fqd7Q2qkLm9UT
+ppWD+hr5/Gp6glt7fztYY9Z/t05UT2href7C9UT2nKRA0AwIQeAYEIOAMGEHACCCTkABBNyAAgm
5AAQTMgBINiwsLhfvaG15csb1RPaGo2qF/Q1nj+qntDWo83Xqie09XRvqXpCW9sehJnJRQ4AwYQc
AIIJOQAEE3IACCbkABBMyAEgmJADQDAhB4BgQg4AwYaDg/nqDa3NXV2rntDWdHG5ekJbyyv/VE9o
a+Xu5eoJbb08HKontLW1r1WzuMgBIJiQA0AwIQeAYEIOAMGEHACCCTkABBNyAAgm5AAQbNh4dKZ6
Q2sXL0yrJ7S1f/G96gltja6/qJ7Q1sWHn1VPaGv5zyvVE9p6drhSPaEtFzkABBNyAAgm5AAQTMgB
IJiQA0AwIQeAYEIOAMGEHACCDT9tnK/e0NrNZ79XT2hrWPN4xSzj8VL1hLbmbn5VPaGts19sV09o
66fHJ6sntOUiB4BgQg4AwYQcAIIJOQAEE3IACCbkABBMyAEgmJADQDAhB4BgwzebC9UbWvvkzr3q
CX3dmqte0NbcsFo9oa29t96vntDWhbMPqif0df9i9YK2XOQAEEzIASCYkANAMCEHgGBCDgDBhBwA
ggk5AAQTcgAINvx4eL96Q2tPf75cPaGthY8fVU9oa2HxTPWEtiZnrlVPaOvc299WT2jrxC83qie0
5SIHgGBCDgDBhBwAggk5AAQTcgAIJuQAEEzIASCYkANAsOGvg1+rN7T2x513qie09e7D36ontDVd
vVo9oa35hdPVE9qav/6kekJb5z/frZ7QloscAIIJOQAEE3IACCbkABBMyAEgmJADQDAhB4BgQg4A
wYQcAIINuweb1Rtau/3wg+oJbd24/WX1hLaOLn1YPaGt6fSoekJbkzeuVE9o68r64+oJbbnIASCY
kANAMCEHgGBCDgDBhBwAggk5AAQTcgAIJuQAEGyYTHarN7R2f2elekJbB9/tV09o6+jG99UT2prO
+07NMjp+qnpCW5def1A9oS0XOQAEE3IACCbkABBMyAEgmJADQDAhB4BgQg4AwYQcAIINo+oFzT3Z
n6ue0Na9H65VT2jrzXOfVk/o68q56gVtjfY80DXL8VPr1RPacpEDQDAhB4BgQg4AwYQcAIIJOQAE
E3IACCbkABBMyAEgmJADQLBhNF6s3tDa+Ni0ekJbz1+sVE9o68Xds9UT2lre3aie0JZfm9mmk9PV
E9pykQNAMCEHgGBCDgDBhBwAggk5AAQTcgAIJuQAEEzIASDYMB55EOZVBn91Zto7WKie0Nb2xpnq
CW1NDueqJ7Q1nptUT2hrb8cDVLPIFAAEE3IACCbkABBMyAEgmJADQDAhB4BgQg4AwYQcAIIN45FH
PV5lGE2rJ7R1OPE/cJbtrbXqCW0d7PnNmWU8d1Q9oa3tZyeqJ7TllxgAggk5AAQTcgAIJuQAEEzI
ASCYkANAMCEHgGBCDgDB/gMdm52/dv0DWAAAAABJRU5ErkJggg==
" transform="translate(22, 120)"/>
 
 
 
 
 
 
 
<image width="18" height="149" xlink:href="data:;base64,
iVBORw0KGgoAAAANSUhEUgAAABIAAACVCAYAAABVe6o3AAABTklEQVRoge3ai00DQQxFUQ8Z+m+C
HonAnzRxhKyIFHD1Ph7vaicn+2sC/G5PCk7cricCNQLNOmujQMFAjTKK/EagddZO/SBQKpBSFF0G
5KzlrwFBa0jRxowagVxGah+p+oMpSqWoWEbkHWJlRmaw46J3iLjBQCaiuNPHgCIRaOpjGShURlMP
BEplbRColSKYkQKNql8panZEVP1sIFvVDzNC9S+01qo1BlLWqtXpV8vfZcRAbLLXWSsFYqefDeRG
a9taK/ZccxkhUCprC+fIgbZtSGhtG2hj/eq5tk4RA6Wrn3De2hpTVOvCRl8P/639KSgVCJ5+BkLf
s9+4fpaR25CBFDFrC+cI3WfcVKBmYa+zVuiG5fZh1tD9Wh1lzYWNrGWgK+hSIJgRU6RAw9aI+o8W
q18pGpcRa01ZYxuS1a8yikHWWP2DNuSJ+CTP7BdYkThsRNHAbQAAAABJRU5ErkJggg==
" transform="translate(532, 120)"/>
 
 
 4000 
 
 
 4500 
 
 
 5000 
 
 
 5500 
 
 
 6000 
 
 
 6500 
 
 
 7000 
 
 
 7500 
 
<polyline clip-path="url(#clip4100)" style="stroke:#000000; stroke-width:1; stroke-opacity:1; fill:none" points="
 550.315,269.364 550.315,259.797 556.315,259.797 550.315,259.797 550.315,240.565 556.315,240.565 550.315,240.565 550.315,221.334 556.315,221.334 550.315,221.334 
 550.315,202.103 556.315,202.103 550.315,202.103 550.315,182.871 556.315,182.871 550.315,182.871 550.315,163.64 556.315,163.64 550.315,163.64 550.315,144.408 
 556.315,144.408 550.315,144.408 550.315,125.177 556.315,125.177 550.315,125.177 550.315,120.37 
 "/>

min value = 3751.255413440107
max value = 7624.981127388768
Reward function for the 1 link acrobot:


<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 -10 
 
 
 -5 
 
 
 0 
 
 
 5 
 
 
 10 
 
 
 1 
 
 
 2 
 
 
 3 
 
 
 4 
 
 
 5 
 
 
 6 
 
 
<image width="498" height="149" xlink:href="data:;base64,
iVBORw0KGgoAAAANSUhEUgAAAfIAAACVCAYAAACjF3iGAAAEwklEQVR4nO3cv2plVRjG4eycfZJz
ZjKGOMgUA4IgWFpbWWkxjYXYiaWFd+AVeAcW1laKhY2FnZXXIAhWUwwyBJ0/Oflzsr2ClcLm+154
nit4CYv1O6vIng4O5uWAoS/f+qp6QlsfPz6vntDWo/svqie09ezVg+oJbf369Kx6Qlvf/f1t9YS2
DqsHAAD/n5ADQDAhB4BgQg4AwYQcAIIJOQAEE3IACCbkABBMyAEg2Lye36ze0NrpkQ/fjZwe76on
tHWyfV09oa3dzbp6QlvumzGtGvMiB4BgQg4AwYQcAIIJOQAEE3IACCbkABBMyAEgmJADQLB5Mz+s
3tDaG+vb6gltnRxfVE9o697W32bk5OqoekJb7psxrRrzIgeAYEIOAMGEHACCCTkABBNyAAgm5AAQ
TMgBIJiQA0Cwebs6rd7Q2v3ZBxpGtseX1RPa2mx31RPa2u421RPact+MadWYFzkABBNyAAgm5AAQ
TMgBIJiQA0AwIQeAYEIOAMGEHACCCTkABJs304PqDa1tV/vqCW0dHV1VT2jraOOrdyPOzZj7Zkyr
xrzIASCYkANAMCEHgGBCDgDBhBwAggk5AAQTcgAIJuQAEGz64f0vluoRnX3y+U/VE9q6/uxJ9YS2
Dh99UD2hrdtnv1dPaGv94y/VE9r6+ftPqye05UUOAMGEHACCCTkABBNyAAgm5AAQTMgBIJiQA0Aw
IQeAYPP6cF+9obVp7e8zsqzvVU9oazWfVE9oa+/cDLlvxrRqzIscAIIJOQAEE3IACCbkABBMyAEg
mJADQDAhB4BgQg4AwYQcAILNq2mp3tDbXD2gsdVx9YK2Dleb6gl9OTdj7pshrRrzIgeAYEIOAMGE
HACCCTkABBNyAAgm5AAQTMgBIJiQA0CwefJP9nebqgf0tUyr6gltTZPfyCPOzR3cN0NaNea2AYBg
Qg4AwYQcAIIJOQAEE3IACCbkABBMyAEgmJADQLB5WXyB4E6+QTA0LfvqCW0ty231hLacmzu4b4a0
asyLHACCCTkABBNyAAgm5AAQTMgBIJiQA0AwIQeAYEIOAMGEHACCzXtfy7nbTfWAxvaX1Qvaut3v
qif05dyMuW+GtGrMixwAggk5AAQTcgAIJuQAEEzIASCYkANAMCEHgGBCDgDB5uvbVfWG1pZrf5+R
6fp19YS29jcvqye05dyMuW/GtGrMixwAggk5AAQTcgAIJuQAEEzIASCYkANAMCEHgGBCDgDBprdP
PlqqR3T29eN3qie09eG7f1RPaOvs4Xn1hLbOn59VT2jrtz/fq57Q1jdP/6qe0JYXOQAEE3IACCbk
ABBMyAEgmJADQDAhB4BgQg4AwYQcAIIJOQAEm3fLi+oNrV3sV9UT2rq6Oqqe0NbV7rh6QlvOzZj7
ZkyrxrzIASCYkANAMCEHgGBCDgDBhBwAggk5AAQTcgAIJuQAEGy+2P9TvaG1Vzd+64xcXProycj2
YlM9oS3nZsx9M6ZVY04NAAQTcgAIJuQAEEzIASCYkANAMCEHgGBCDgDBhBwAgs27m+fVG1r799pv
nZGXl9vqCW1tLq6qJ7Tl3Iy5b8a0asypAYBgQg4AwYQcAIIJOQAEE3IACCbkABBMyAEgmJADQLD/
ADLBmm0TyYM1AAAAAElFTkSuQmCC
" transform="translate(22, 119)"/>
 
 
 
 
 
 
 
<image width="18" height="149" xlink:href="data:;base64,
iVBORw0KGgoAAAANSUhEUgAAABIAAACVCAYAAABVe6o3AAABTklEQVRoge3ai00DQQxFUQ8Z+m+C
HonAnzRxhKyIFHD1Ph7vaicn+2sC/G5PCk7cricCNQLNOmujQMFAjTKK/EagddZO/SBQKpBSFF0G
5KzlrwFBa0jRxowagVxGah+p+oMpSqWoWEbkHWJlRmaw46J3iLjBQCaiuNPHgCIRaOpjGShURlMP
BEplbRColSKYkQKNql8panZEVP1sIFvVDzNC9S+01qo1BlLWqtXpV8vfZcRAbLLXWSsFYqefDeRG
a9taK/ZccxkhUCprC+fIgbZtSGhtG2hj/eq5tk4RA6Wrn3De2hpTVOvCRl8P/639KSgVCJ5+BkLf
s9+4fpaR25CBFDFrC+cI3WfcVKBmYa+zVuiG5fZh1tD9Wh1lzYWNrGWgK+hSIJgRU6RAw9aI+o8W
q18pGpcRa01ZYxuS1a8yikHWWP2DNuSJ+CTP7BdYkThsRNHAbQAAAABJRU5ErkJggg==
" transform="translate(532, 119)"/>
 
 
 20 
 
 
 30 
 
 
 40 
 
 
 50 
 
 
 60 
 
 
 70 
 
 
 80

min reward = 17.730395598910633
max reward = 80.0


Here we can clearly see that the equilibrium state is at $(\pi,0)$ which is preserved after value iteration in the value function. We can see the trajectory of the one-link pendulum driven by the newly computed policy:

In [244]:
anim(init_diagonal(Val{1}), sim1, get_optimal_policy(vi1), advance, "discrete_vi_one_link6", 500)

### Two-link Acrobot

Let's define a few utility functions that will help us look at the data.
The following routines will plot the rewards function against angles at zero angular velocity (`plot_rewards_θ`), which should show a maximum reward at the unstable equilibrium state and against velocities at $\theta = (\pi,\pi)$ (`plot_rewards_ω`), which should show show a maximum reward at zero angular velocity (at least the first angular velocity). This will help us identify if the reward function is accurate:

In [267]:
function plot_rewards_θ(vi::ValueIteration{4}, sim::Simulation{2})
    idxs = 1:vi.grid.nθs
    ω_mid_idx = iω(vi.grid, 0.0)
    rew(i,j) = reward(state_at(vi.grid, SVector(i,ω_mid_idx,j,ω_mid_idx)),
                      sim, vi.grid.ω_limit, vi.boundary_penalty)
    reward_mtx = reshape([rew(i,j) for j in idxs for i in idxs], vi.grid.nθs, vi.grid.nθs)
    display(heatmap(θ.(vi.grid, 1:vi.grid.nθs), θ.(vi.grid, 1:vi.grid.nθs), reward_mtx, aspect_ratio=1))
    println("min reward = ", minimum(reward_mtx))
    println("max reward = ", maximum(reward_mtx))
end
function plot_rewards_ω(vi::ValueIteration{4}, sim::Simulation{2})
    idxs = 1:vi.grid.nωs
    θ_mid_idx = iθ(vi.grid, 1π)
    rew(i,j) = reward(state_at(vi.grid, SVector(θ_mid_idx,i,θ_mid_idx,j)),
                      sim, vi.grid.ω_limit, vi.boundary_penalty)
    reward_mtx = reshape([rew(i,j) for j in idxs for i in idxs], vi.grid.nωs, vi.grid.nωs)
    display(heatmap(ω.(vi.grid, 1:vi.grid.nωs), ω.(vi.grid, 1:vi.grid.nωs), reward_mtx, aspect_ratio=1))
    println("min reward = ", minimum(reward_mtx))
    println("max reward = ", maximum(reward_mtx))
end;

The next function will plot the optimal value function and policy at zero angular velocity this may help identify further problems in our solution.

In [268]:
# plot value function and find minimum and maximum values
function show_solution(vi::ValueIteration{4}, sim::Simulation{2})
    println("Value function for the 2 link acrobot at zero angular velocity:")
    flush(STDOUT)
    ω_mid_idx = iω(vi.grid,0.0)
    display(heatmap(θ.(vi.grid, 1:vi.grid.nθs), θ.(vi.grid, 1:vi.grid.nθs),
                    vi.V[:,ω_mid_idx,:,ω_mid_idx], aspect_ratio=1))
    println("min value = ", minimum(vi.V))
    println("max value = ", maximum(vi.V))
    println("Policy for the 2 link acrobot at zero angular velocity:")
    flush(STDOUT)
    display(heatmap(θ.(vi.grid, 1:vi.grid.nθs), θ.(vi.grid, 1:vi.grid.nθs),
                    vi.μ[:,ω_mid_idx,:,ω_mid_idx], aspect_ratio=1))
    println("min torque = ", minimum(vi.μ))
    println("max torque = ", maximum(vi.μ))
    
    println("Value function for the 2 link acrobot in unstable equilibrium:")
    flush(STDOUT)
    θ_mid_idx = iθ(vi.grid, 1π)
    display(heatmap(ω.(vi.grid, 1:vi.grid.nωs), ω.(vi.grid, 1:vi.grid.nωs),
                    vi.V[θ_mid_idx,:,θ_mid_idx,:], aspect_ratio=1))
    println("min value = ", minimum(vi.V))
    println("max value = ", maximum(vi.V))
    println("Policy for the 2 link acrobot  in unstable equilibrium:")
    flush(STDOUT)
    display(heatmap(ω.(vi.grid, 1:vi.grid.nωs), ω.(vi.grid, 1:vi.grid.nωs),
                    vi.μ[θ_mid_idx,:,θ_mid_idx,:], aspect_ratio=1))
    println("min torque = ", minimum(vi.μ))
    println("max torque = ", maximum(vi.μ))
end;

Finally, the following routine will save our result (using the `JLD.jl` module) to a given file name under the data subdirectory, which can be subsequently loaded with `JLD.load`:

In [242]:
function save_result(filename, vi)
    save("./data/" * filename * ".jld", "vi", vi)
end;

To start we will run a low resolution simulation to check that everthing compiles and works as expected:

In [243]:
@time vi2, sim2 = begin
    vi = ValueIteration{4}(StateGrid(;nθs=12,nωs=11,nτs=9,ω_lim=11.0,τ_lim=11.0), γ=0.99, bdry_penalty=-30)
    init(vi)
    sim = Simulation{2}(ACROBOT)
    train_vi(vi, sim);
    print("The state space is discretized into a finite number ");
    println("of angles, angular velocities and torques as follows")
    println("θ = ", θ.(vi.grid, 1:vi.grid.nθs))
    println("ω = ", ω.(vi.grid, 1:vi.grid.nωs))
    println("τ = ", τ.(vi.grid, 1:vi.grid.nτs))
    vi, sim
end;

Progress: ==================================================> 100%; residual = 1.0132487134343426e-5   
final residual = 9.871142198684113e-6
The state space is discretized into a finite number of angles, angular velocities and torques as follows
θ = [0.523599, 1.0472, 1.5708, 2.0944, 2.61799, 3.14159, 3.66519, 4.18879, 4.71239, 5.23599, 5.75959, 6.28319]
ω = [-11.0, -8.8, -6.6, -4.4, -2.2, 0.0, 2.2, 4.4, 6.6, 8.8, 11.0]
τ = [-11.0, -8.25, -5.5, -2.75, 0.0, 2.75, 5.5, 8.25, 11.0]
1865.930216 seconds (3.99 M allocations: 383.604 MiB, 0.01% gc time)


Let's take a look at the rewards function:

In [269]:
plot_rewards_θ(vi2, sim2) # Recall that θ₁ and ω₁ are on the y axis

<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 1 
 
 
 2 
 
 
 3 
 
 
 4 
 
 
 5 
 
 
 6 
 
 
 1 
 
 
 2 
 
 
 3 
 
 
 4 
 
 
 5 
 
 
 6 
 
 
<image width="366" height="366" xlink:href="data:;base64,
iVBORw0KGgoAAAANSUhEUgAAAW4AAAFuCAYAAAChovKPAAAH7ElEQVR4nO3WT65lVRmH4W/fc4oq
ikIxVMQ/XVsGW8aGbedg4qAcjjFxDiYYtWeCJkbQlAKCVEHde7eNYgQ2+PLG55nALztnnXet4zge
nbPkOK47u3OzsvtqfGd79Zv/D51zvzS8tDt733yetyu7m9v+zQAxwg0QI9wAMcINECPcADHCDRAj
3AAxwg0QI9wAMcINECPcADHCDRAj3AAxwg0QI9wAMcINECPcADHCDRAj3AAxwg0QI9wAMcINECPc
ADHCDRAj3AAxwg0QI9wAMcINECPcADHCDRBzPY7r2vgxO9vHcVnZfWXnrjyOY2X3q/Wl3XNpd2bO
pe3jfmd3Zua829ndPNpLvLgBYoQbIEa4AWKEGyBGuAFihBsgRrgBYoQbIEa4AWKEGyBGuAFihBsg
RrgBYoQbIEa4AWKEGyBGuAFihBsgRrgBYoQbIEa4AWKEGyBGuAFihBsgRrgBYoQbIEa4AWKEGyBG
uAFirsdc18aPY2f7OC4ru6+2d+7Kwx39tTqP+53dc2f3lWNn9tyZnZm1T/ZvBogRboAY4QaIEW6A
GOEGiBFugBjhBogRboAY4QaIEW6AGOEGiBFugBjhBogRboAY4QaIEW6AGOEGiBFugBjhBogRboAY
4QaIEW6AGOEGiBFugBjhBogRboAY4QaIEW6AGOEGiBFugJjrcVzWxre2f/uzd1d2Z2Zef/3Fyu7l
5m5ld2bm5csHK7v/+fzxyu7MzMf/ebKy+68Xe9/8iz/8Zmn5XNqdmfN+ZdaLGyBGuAFihBsgRrgB
YoQbIEa4AWKEGyBGuAFihBsgRrgBYoQbIEa4AWKEGyBGuAFihBsgRrgBYoQbIEa4AWKEGyBGuAFi
hBsgRrgBYoQbIEa4AWKEGyBGuAFihBsgRrgBYoQbIOb4y89/cm6NP3n60cruo6efrOzOzDx459OV
3eO6MjszM+eLnd27Tx7vDM/Mi2ffXNn9+G/fXtmdmXn++esru7d3e4f75uZuZ3dlFYD/mXADxAg3
QIxwA8QIN0CMcAPECDdAjHADxAg3QIxwA8QIN0CMcAPECDdAjHADxAg3QIxwA8QIN0CMcAPECDdA
jHADxAg3QIxwA8QIN0CMcAPECDdAjHADxAg3QIxwA8QIN0CMcAPEHF/88vG5NX757s69cb7zzsru
zMzL7/9gZfe8vLayOzNz88VnK7uXf36wsjszc/P3D1d27/58u7I7M3P778cru/cvryu7MzPH5W5l
14sbIEa4AWKEGyBGuAFihBsgRrgBYoQbIEa4AWKEGyBGuAFihBsgRrgBYoQbIEa4AWKEGyBGuAFi
hBsgRrgBYoQbIEa4AWKEGyBGuAFihBsgRrgBYoQbIEa4AWKEGyBGuAFihBsg5nr53mVv/bXXdnaP
Y2d3Zu4fPtnZffqjld2ZmYdPfrCy+/lnf1rZnZm5efb7ld2HT3+3sjsz8/Cjj3aGv3y+szszc72u
zHpxA8QIN0CMcAPECDdAjHADxAg3QIxwA8QIN0CMcAPECDdAjHADxAg3QIxwA8QIN0CMcAPECDdA
jHADxAg3QIxwA8QIN0CMcAPECDdAjHADxAg3QIxwA8QIN0CMcAPECDdAjHADxAg3QMz1+Xtvro3f
PLhd2b1+48OV3ZmZR8+erezev/PHld2ZmZdvf3dl9/LwycruzMxx9+XO8Hnu7M7MfPHFyuzdB/cr
uzMzL//5eGXXixsgRrgBYoQbIEa4AWKEGyBGuAFihBsgRrgBYoQbIEa4AWKEGyBGuAFihBsgRrgB
YoQbIEa4AWKEGyBGuAFihBsgRrgBYoQbIEa4AWKEGyBGuAFihBsgRrgBYoQbIEa4AWKEGyDm+v57
P9wbv9yu7L7++PnK7szMW3/9x8ruo6c7uzMzl2/+eWX3+mhldmZmzp2jPV/+/c2d4Zl58ew7K7uf
PfvWyu7MzKefPlnZ9eIGiBFugBjhBogRboAY4QaIEW6AGOEGiBFugBjhBogRboAY4QaIEW6AGOEG
iBFugBjhBogRboAY4QaIEW6AGOEGiBFugBjhBogRboAY4QaIEW6AGOEGiBFugBjhBogRboAY4QaI
EW6AmON6eftcGz+uK7s3x2Vld2bm1z/+6cruW298trI7M/PG489Xdh88eLmyOzNzd79zxt791fsr
uzMz9+fdyu553q7svtreOWNe3AAxwg0QI9wAMcINECPcADHCDRAj3AAxwg0QI9wAMcINECPcADHC
DRAj3AAxwg0QI9wAMcINECPcADHCDRAj3AAxwg0QI9wAMcINECPcADHCDRAj3AAxwg0QI9wAMcIN
ECPcADHH5eatc238uC7tXlZ2X23v3JWHO/prdc79zu65s/tq+25p93Zld2bmnJ1t/2aAGOEGiBFu
gBjhBogRboAY4QaIEW6AGOEGiBFugBjhBogRboAY4QaIEW6AGOEGiBFugBjhBogRboAY4QaIEW6A
GOEGiBFugBjhBogRboAY4QaIEW6AGOEGiBFugBjhBogRboAY4QaIuZ5zu7d+/t8Nz3nu3JXHcazs
frW+tLv5O29t3y/tzpzn3c7uYsPOc2fbixsgRrgBYoQbIEa4AWKEGyBGuAFihBsgRrgBYoQbIEa4
AWKEGyBGuAFihBsgRrgBYoQbIEa4AWKEGyBGuAFihBsgRrgBYoQbIEa4AWKEGyBGuAFihBsgRrgB
YoQbIEa4AWKEGyDmv+6WtiVvFsRYAAAAAElFTkSuQmCC
" transform="translate(88, 12)"/>
 
 
 
 
 
 
 
<image width="18" height="366" xlink:href="data:;base64,
iVBORw0KGgoAAAANSUhEUgAAABIAAAFuCAYAAACMWUhZAAACFUlEQVR4nO2cwXHDMAwEwYz6r8Jd
xgFSAv3Yx/oGLOBGeweAlGTrvPs1BawfQqSq6ul5M0IDCXFo07lom9pdKNejojyihEA0KjUhGpfa
LyS0lX1bHNqZP0aomhEC0aArwtCegswO9mjR7us53YwQV9lCjzA0xmwlmi01rCDBFrHFDzatDw1K
jYo/OLXk+KuRB1roHWRwaozZ2ZUt84hEkwmRT/0goWCPODSmQ9D4DyNkTA1Cm8E8YoSCPRKiVTMX
Rb6EkhUkNkbIwyijJUQDZ/ZW9k1o1qPbIiubalrddoQ17VCDzRh/7GlkK/sDIWqwBc9s4WlkU/s+
IWH3N7SvGeMPblqbkNCjzkULTk0nRP70PBYNbNrY7Sg4/mA0XfwgWsnQhPFDL9edaFT8UB1t094X
iIbIZFc2NSGFaNRgE25HuhYJ7n4jmm4eQa2GDjZmCQdbMFrwzMbO2cbDKCQUPdgYIbBpudMIomPc
ssH7fkQHjR8SMqLZZrZxy5YJBW/ZwdvRenRfO7PvyzdqhfEP9DcfJRoktGh3IWH3U5UdjOa7OxrI
bW5fM3Z/7MzmmhYSEqJxQlCvGSt7478tMjXoOxGcR8f2VYbmPLKhcfEfW2XrUsPMJj2CPqRkrOxY
NLAgYz3C0IRNS33+yoc2NjSsjjb++yLjt6UmrGzoiowzW4iGpaarbAqtqMeHlTvYhGhc/LlokNA/
te/n6yXzS78AAAAASUVORK5CY

min reward = -214.73920880217872
max reward = 119.99999999999999


In [270]:
plot_rewards_ω(vi2, sim2)

<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 -10 
 
 
 -5 
 
 
 0 
 
 
 5 
 
 
 10 
 
 
 -10 
 
 
 -5 
 
 
 0 
 
 
 5 
 
 
 10 
 
 
<image width="364" height="364" xlink:href="data:;base64,
iVBORw0KGgoAAAANSUhEUgAAAWwAAAFsCAYAAADon4O5AAAFZElEQVR4nO3WsUkFQQBF0V2ZSFuw
AkHswcjYFmzth2JsH4KxgWV8WEvYycYL51Twosvbt20cGwD/3s3qAQDMEWyACMEGiBBsgAjBBogQ
bIAIwQaIEGyACMEGiBBsgAjBBogQbIAIwQaIEGyACMEGiBBsgAjBBogQbIAIwQaIEGyACMEGiBBs
gAjBBogQbIAIwQaIEGyACMEGiBBsgAjBBogQbIAIwQaIEGyACMEGiBjPt2+rNwAwwcMGiBBsgAjB
BogQbIAIwQaIEGyACMEGiBBsgAjBBogQbIAIwQaIEGyACMEGiBBsgAjBBogQbIAIwQaIEGyACMEG
iBBsgAjBBogQbIAIwQaIEGyACMEGiBBsgAjBBogQbIAIwQaIEGyACMEGiBBsgIjxer96AgAzPGyA
CMEGiBBsgAjBBogQbIAIwQaIEGyACMEGiBBsgAjBBogQbIAIwQaIEGyACMEGiBBsgAjBBogQbIAI
wQaIEGyACMEGiBBsgAjBBogQbIAIwQaIEGyACMEGiBBsgAjBBogQbIAIwQaIEGyACMEGiBgvD1+r
NwAwwcMGiBBsgAjBBogQbIAIwQaIEGyACMEGiBBsgAjBBogQbIAIwQaIEGyACMEGiBBsgAjBBogQ
bIAIwQaIEGyACMEGiBBsgAjBBogQbIAIwQaIEGyACMEGiBBsgAjBBogQbIAIwQaIEGyACMEGiBBs
gIj9erk7Vo8A4JyHDRAh2AARgg0QIdgAEYINECHYABGCDRAh2AARgg0QIdgAEYINECHYABGCDRAh
2AARgg0QIdgAEYINECHYABGCDRAh2AARgg0QIdgAEYINECHYABGCDRAh2AARgg0QIdgAEYINECHY
ABGCDRAh2AAR+/W4HKtHAHDOwwaIEGyACMEGiBBsgAjBBogQbIAIwQaIEGyACMEGiBBsgAjBBogQ
bIAIwQaIEGyACMEGiBBsgAjBBogQbIAIwQaIEGyACMEGiBBsgAjBBogQbIAIwQaIEGyACMEGiBBs
gAjBBogQbIAIwQaIEGyAiP16uTtWjwDgnIcNECHYABGCDRAh2AARgg0QIdgAEYINECHYABGCDRAh
2AARgg0QIdgAEYINECHYABGCDRAh2AARgg0QIdgAEYINECHYABGCDRAh2AARgg0QIdgAEYINECHY
ABGCDRAh2AARgg0QIdgAEYINECHYABHj5/1p9QYAJnjYABGCDRAh2AARgg0QIdgAEYINECHYABGC
DRAh2AARgg0QIdgAEYINECHYABGCDRAh2AARgg0QIdgAEYINECHYABGCDRAh2AARgg0QIdgAEYIN
ECHYABGCDRAh2AARgg0QIdgAEYINECHYABGCDRAxPr8fV28AYIKHDRAh2AARgg0QIdgAEYINECHY
ABGCDRAh2AARgg0QIdgAEYINECHYABGCDRAh2AARgg0QIdgAEYINECHYABGCDRAh2AARgg0QIdgA
EYINECHYABGCDRAh2AARgg0QIdgAEYINECHYABGCDRAh2AAR4+N39QQAZnjYABGCDRAh2AARgg0Q
IdgAEYINECHYABGCDRAh2AARgg0QIdgAEYINECHYABGCDRAh2AARgg0QIdgAEYINECHYABGCDRAh
2AARgg0QIdgAEYINECHYABGCDRAh2AARgg0QIdgAEYINECHYABGCDRCxb9s4Vo8A4JyHDRAh2AAR
gg0QIdgAEYINECHYABGCDRAh2AARgg0QIdgAEYINECHYABGCDRAh2AARgg0QIdgAEYINECHYABGC
DRAh2AARgg0QIdgAEYINECHYABGCDRAh2AARgg0QIdgAEYINECHYABGCDRAh2AARf6C3FULJOkKn
AAAAAElFTkSuQmCC
" transform="translate(96, 12)"/>
 
 
 
 
 
 
 
<image width="18" height="364" xlink:href="data:;base64,
iVBORw0KGgoAAAANSUhEUgAAABIAAAFsCAYAAADBkelSAAACHUlEQVR4nO2c223EMAwEqUD9V5Eu
4yOvBPpjEAwIqoCF9kU5vljnyd8KYP0QIBERN+thgAoC4qhVzqVmcw0Te7BGHLWgkk0BgdQo1yZr
lH8Q0Ca7Wxy1Ux8GKBICOhAQaT+lESQ2aD9Gbe1vgU4mAiSkRgEpk824NjnZRvsh1yj7la6N1Qi0
35ZsnWtC+yORF1pxo3zUMNcYjZTUVqMeCMFBqUFAUGeN1HRA5Ds2CKjyIEBK+xlqt8qnEUSNAiLf
+Y+lFslgTdaImkc3itmUkJpxZm+ym3XLppHwOKI0Eh5HXPt1gw2035Zs0P6x7QeT7aO2rrVAtooY
2++z33aukf8PKSutUKNN9j8C5WrUraXWL18gZ2s09mlk8DzaZPdAQvtDRk1oP/TjupMaZT+Uo8Gl
NdpPAQmpYa7pks2VFhtsOo249iMwS+3NMs5sBEbZ/qXWA/ke2AfPbIya8WEUAtJVZO3vF2g/g6Oc
2XM1AqnZkg0eRxAQtSOlRmt/s4TUVqMXQAyOcmbr5pFu1N6CPqoRJntwaXU5MrZfl+zB1MCfM6Dv
sn3n2s7sF0A6apTYGDWhRkmVVpjswa5R1Ar6etmo0cGo2a4JoXYE2n909nPJttkPltZ2/xGYbOge
LZ/9Oo2WWr/A0kI34GA7Iv/KnksNm0eDNeKo6dq/rvVAVEWoHQmHf+kumcaoBfQmArwngnON0sjX
fs7+udQgoC/rNOfnsknqIwAAAABJRU5ErkJggg==
" transform="translate(472, 12)"/>
 
 
 - 
 
 
 300 
 
 
 - 
 
 
 250 
 
 
 - 
 
 
 200 
 
 
 - 
 
 
 150 
 
 
 - 
 
 
 100 
 
 
 - 
 
 
 50 
 
 
 0 
 
 
 50 
 
 
 100 
 
<polyline clip-path="url(#clip5900)" style="stroke:#000000; stroke-width:1; stroke-opacity:1; fill:none" points="
 490.083,375.813 490.083,359.268 496.083,359.268 490.083,359.268 490.083,317.904 496.083,317.904 490.083,317.904 490.083,276.54 496.083,276.54 490.083,276.54 
 490.083,235.176 496.083,235.176 490.083,235.176 490.083,193.812 496.083,193.812 490.083,193.812 490.083,152.448 496.083,152.448 490.083,152.448 490.083,111.084 
 496.083,111.084 490.083,111.084 490.083,69.7205 496.083,69.7205 490.083,69.7205 490.083,28.3566 496.083,28.3566 490.083,28.3566 490.083,11.811 
 "/>

min reward = -320.0
max reward = 119.99999999999999


As expected the maximum rewards is attained at $(\pi, \pi)$ and zero angular velocity $\omega_1$. We chose not to penalize $\omega_2$ here. Now lets look at the optimal value function and optimal policy to check that maximums are attained were expected as before:

In [256]:
show_solution(vi2, sim2) # Recall that θ₁ and ω₁ are on the y axis

Value function for the 2 link acrobot at zero angular velocity:


<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 1 
 
 
 2 
 
 
 3 
 
 
 4 
 
 
 5 
 
 
 6 
 
 
 1 
 
 
 2 
 
 
 3 
 
 
 4 
 
 
 5 
 
 
 6 
 
 
<image width="498" height="364" xlink:href="data:;base64,
iVBORw0KGgoAAAANSUhEUgAAAfIAAAFsCAYAAAA3/TvjAAAHiklEQVR4nO3XvY5VVRyH4X3wMHzI
oEYcMJEPg4OF3ICJnTEmVl6GhVfjvVhZGysbEy1AEAImMhgNDjgjEI5XYPYOzZrXPM8V/JqVd/1X
07TeTABA0rHRAwCAlyfkABAm5AAQJuQAECbkABAm5AAQJuQAECbkABAm5AAQJuQAECbkABAm5AAQ
JuQAECbkABAm5AAQJuQAECbkABAm5AAQJuQAECbkABAm5AAQJuQAECbkABAm5AAQJuQAECbkABAm
5AAQJuQAECbkABAm5AAQJuQAECbkABAm5AAQJuQAECbkABAm5AAQJuQAECbkABAm5AAQJuQAECbk
ABAm5AAQJuQAECbkABAm5AAQJuQAECbkABAm5AAQJuQAECbkABAm5AAQJuQAECbkABAm5AAQJuQA
ECbkABAm5AAQJuQAECbkABAm5AAQJuQAECbkABAm5AAQJuQAECbkABAm5AAQJuQAECbkABAm5AAQ
JuQAECbkABAm5AAQJuQAECbkABAm5AAQJuQAECbkABAm5AAQJuQAECbkABAm5AAQJuQAECbkABAm
5AAQJuQAECbkABAm5AAQJuQAECbkABAm5AAQJuQAECbkABAm5AAQJuQAECbkABAm5AAQJuQAECbk
ABAm5AAQJuQAECbkABAm5AAQJuQAECbkABAm5AAQJuQAECbkABAm5AAQJuQAECbkABAm5AAQJuQA
ECbkABAm5AAQJuQAECbkABAm5AAQJuQAECbkABAm5AAQJuQAELbePrk7esMib6wvjp4w6+qLd0dP
WOTK6ROjJ8w6e3z0gmX2n41eMO/+QWDkNE23VvdGT5i19/zW6AmL7B/eHD1h1rFV45GfOXFl9IRZ
LnIACBNyAAgTcgAIE3IACBNyAAgTcgAIE3IACBNyAAgTcgAIE3IACBNyAAgTcgAIE3IACBNyAAgT
cgAIE3IACBNyAAgTcgAIE3IACBNyAAgTcgAIE3IACBNyAAgTcgAIE3IACBNyAAgTcgAIE3IACBNy
AAhbfbX7xWb0iCU+ePPh6AmzLp3/bfSERd6+/vPoCbO2dh6NnrDIs4dnR0+Y9fuNy6MnLHLj7tHf
+d2D86MnLHJ7/5XRE2a9vjV6wTK724ejJ8xykQNAmJADQJiQA0CYkANAmJADQJiQA0CYkANAmJAD
QJiQA0CYkANAmJADQJiQA0CYkANAmJADQJiQA0CYkANAmJADQJiQA0CYkANAmJADQJiQA0CYkANA
mJADQJiQA0CYkANAmJADQJiQA0CYkANAmJADQNjq+48/3YwescT2mSejJ8y68N7d0RMWOfXZ1ugJ
sw6ufzJ6wiKndz4aPWHW33vfjp6wyKkfvxk9YdbB1/+MnrDIg1uXRk+Y9fjxq6MnLLLZrEZPmOUi
B4AwIQeAMCEHgDAhB4AwIQeAMCEHgDAhB4AwIQeAMCEHgDAhB4AwIQeAMCEHgDAhB4AwIQeAMCEH
gDAhB4AwIQeAMCEHgDAhB4AwIQeAMCEHgDAhB4AwIQeAMCEHgDAhB4AwIQeAMCEHgDAhB4AwIQeA
MCEHgLDV52e/3IwescT2+uj/OXa3X4yesMiHFx6MnjDr2uU7oycscu7a3dETZh1/66/RExZ5uvfa
6Amz7v/w/ugJi9zb2xk9YdZPf5wbPWGRm/tboyfMOvp1BAD+k5ADQJiQA0CYkANAmJADQJiQA0CY
kANAmJADQJiQA0CYkANAmJADQJiQA0CYkANAmJADQJiQA0CYkANAmJADQJiQA0CYkANAmJADQJiQ
A0CYkANAmJADQJiQA0CYkANAmJADQJiQA0CYkANAmJADQNhqmtab0SP+L86cvDp6wiLn17ujJ8y6
urk4esIi75w6PnrCrO2jP3Gapml69HT0gnl3Dg5HT1jk9rFfRk+Y9efze6MnLPLk6a+jJ8xykQNA
mJADQJiQA0CYkANAmJADQJiQA0CYkANAmJADQJiQA0CYkANAmJADQJiQA0CYkANAmJADQJiQA0CY
kANAmJADQJiQA0CYkANAmJADQJiQA0CYkANAmJADQJiQA0CYkANAmJADQJiQA0CYkANAmJADQNhq
mtab0SMAgJfjIgeAMCEHgDAhB4AwIQeAMCEHgDAhB4AwIQeAMCEHgDAhB4AwIQeAMCEHgDAhB4Aw
IQeAMCEHgDAhB4AwIQeAMCEHgDAhB4AwIQeAMCEHgDAhB4AwIQeAMCEHgDAhB4AwIQeAMCEHgDAh
B4AwIQeAMCEHgDAhB4AwIQeAMCEHgDAhB4AwIQeAMCEHgDAhB4AwIQeAMCEHgDAhB4AwIQeAMCEH
gDAhB4AwIQeAMCEHgDAhB4AwIQeAMCEHgDAhB4AwIQeAMCEHgDAhB4AwIQeAMCEHgDAhB4AwIQeA
MCEHgDAhB4AwIQeAMCEHgDAhB4AwIQeAMCEHgDAhB4AwIQeAMCEHgDAhB4AwIQeAMCEHgDAhB4Aw
IQeAMCEHgDAhB4AwIQeAMCEHgDAhB4AwIQeAMCEHgDAhB4AwIQeAMCEHgDAhB4AwIQeAMCEHgDAh
B4AwIQeAMCEHgDAhB4AwIQeAMCEHgDAhB4CwfwFwy1eOcMOTygAAAABJRU5ErkJggg==
" transform="translate(22, 12)"/>
 
 
 
 
 
 
 
<image width="18" height="364" xlink:href="data:;base64,
iVBORw0KGgoAAAANSUhEUgAAABIAAAFsCAYAAADBkelSAAACHUlEQVR4nO2c223EMAwEqUD9V5Eu
4yOvBPpjEAwIqoCF9kU5vljnyd8KYP0QIBERN+thgAoC4qhVzqVmcw0Te7BGHLWgkk0BgdQo1yZr
lH8Q0Ca7Wxy1Ux8GKBICOhAQaT+lESQ2aD9Gbe1vgU4mAiSkRgEpk824NjnZRvsh1yj7la6N1Qi0
35ZsnWtC+yORF1pxo3zUMNcYjZTUVqMeCMFBqUFAUGeN1HRA5Ds2CKjyIEBK+xlqt8qnEUSNAiLf
+Y+lFslgTdaImkc3itmUkJpxZm+ym3XLppHwOKI0Eh5HXPt1gw2035Zs0P6x7QeT7aO2rrVAtooY
2++z33aukf8PKSutUKNN9j8C5WrUraXWL18gZ2s09mlk8DzaZPdAQvtDRk1oP/TjupMaZT+Uo8Gl
NdpPAQmpYa7pks2VFhtsOo249iMwS+3NMs5sBEbZ/qXWA/ke2AfPbIya8WEUAtJVZO3vF2g/g6Oc
2XM1AqnZkg0eRxAQtSOlRmt/s4TUVqMXQAyOcmbr5pFu1N6CPqoRJntwaXU5MrZfl+zB1MCfM6Dv
sn3n2s7sF0A6apTYGDWhRkmVVpjswa5R1Ar6etmo0cGo2a4JoXYE2n909nPJttkPltZ2/xGYbOge
LZ/9Oo2WWr/A0kI34GA7Iv/KnksNm0eDNeKo6dq/rvVAVEWoHQmHf+kumcaoBfQmArwngnON0sjX
fs7+udQgoC/rNOfnsknqIwAAAABJRU5ErkJggg==
" transform="translate(532, 12)"/>
 
 
 500 
 
 
 1000 
 
 
 1500 
 
 
 2000 
 
 
 2500 
 
 
 3000 
 
 
 3500 
 
 

min value = 30.0
max value = 4184.150797027355
Policy for the 2 link acrobot at zero angular velocity:


<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 1 
 
 
 2 
 
 
 3 
 
 
 4 
 
 
 5 
 
 
 6 
 
 
 1 
 
 
 2 
 
 
 3 
 
 
 4 
 
 
 5 
 
 
 6 
 
 
<image width="498" height="364" xlink:href="data:;base64,
iVBORw0KGgoAAAANSUhEUgAAAfIAAAFsCAYAAAA3/TvjAAAG60lEQVR4nO3XIY5WBxSGYX4grcHU
1SBIzSygBKoaxOgqVP1oki6AFXQyDjuCpEE16BG4BjrFsAF8BUFgaP4/lwXQ5N4gOHknz7OCz5y8
ObuLew+XawBA0vXpAQDAlxNyAAgTcgAIE3IACBNyAAgTcgAIE3IACBNyAAgTcgAIE3IACBNyAAgT
cgAIE3IACBNyAAgTcgAIE3IACBNyAAgTcgAIE3IACBNyAAgTcgAIE3IACBNyAAgTcgAIE3IACBNy
AAgTcgAIE3IACBNyAAgTcgAIE3IACBNyAAgTcgAIE3IACBNyAAgTcgAIE3IACBNyAAgTcgAIE3IA
CBNyAAgTcgAIE3IACBNyAAgTcgAIE3IACBNyAAgTcgAIE3IACBNyAAgTcgAIE3IACBNyAAgTcgAI
E3IACBNyAAgTcgAIE3IACBNyAAgTcgAIE3IACBNyAAgTcgAIE3IACBNyAAgTcgAIE3IACBNyAAgT
cgAIE3IACBNyAAgTcgAIE3IACBNyAAgTcgAIE3IACBNyAAgTcgAIE3IACBNyAAgTcgAIE3IACBNy
AAgTcgAIE3IACBNyAAgTcgAIE3IACBNyAAgTcgAIE3IACBNyAAgTcgAIE3IACBNyAAgTcgAIE3IA
CBNyAAgTcgAIE3IACBNyAAgTcgAIE3IACBNyAAgTcgAIE3IACBNyAAgTcgAIE3IACBNyAAgTcgAI
E3IACBNyAAgTcgAIE3IACBNyAAgTcgAIE3IACBNyAAgTcgAIE3IACNvtl6fL9IgtDpdn0xNW3bj7
aHrCJr9+92p6wqpn759MT9hkv5xPT1h1OD2ZnrDJ0eOfpyesevvhYnrClVG4nQofOQCECTkAhAk5
AIQJOQCECTkAhAk5AIQJOQCECTkAhAk5AIQJOQCECTkAhAk5AIQJOQCECTkAhAk5AIQJOQCECTkA
hAk5AIQJOQCECTkAhAk5AIQJOQCECTkAhAk5AIQJOQCECTkAhAk5AIQJOQCECTkAhO0+/v3jMj1i
ixt3H01PgM8cTk+mJ6z695+j6Qmb3P7jzfQEvqL9cj49YZPD5dn0hFU+cgAIE3IACBNyAAgTcgAI
E3IACBNyAAgTcgAIE3IACBNyAAgTcgAIE3IACBNyAAgTcgAIE3IACBNyAAgTcgAIE3IACBNyAAgT
cgAIE3IACBNyAAgTcgAIE3IACBNyAAgTcgAIE3IACBNyAAgTcgAIE3IACNvtl6fL9AioenH/+fSE
Vcev/pyeAFkff/9mesIqHzkAhAk5AIQJOQCECTkAhAk5AIQJOQCECTkAhAk5AIQJOQCECTkAhAk5
AIQJOQCECTkAhAk5AIQJOQCECTkAhAk5AIQJOQCECTkAhAk5AIQJOQCECTkAhAk5AIQJOQCECTkA
hAk5AIQJOQCECTkAhAk5AIQJOQCE3ZweAP/n9Ie/pids8vrd99MTIOnOrePpCZscPZ5esM5HDgBh
Qg4AYUIOAGFCDgBhQg4AYUIOAGFCDgBhQg4AYUIOAGFCDgBhQg4AYUIOAGFCDgBhQg4AYUIOAGFC
DgBhQg4AYUIOAGFCDgBhQg4AYUIOAGFCDgBhQg4AYUIOAGFCDgBhQg4AYUIOAGFCDgBhQg4AYTdf
3H8+veHKePDyl+kJmxwuz6YnrHr97qfpCZs8e/9kesKq/XI+PWGTw+nJ9IRV3/723/SETe7cOp6e
sOrth4vpCVeGjxwAwoQcAMKEHADChBwAwoQcAMKEHADChBwAwoQcAMKEHADChBwAwoQcAMKEHADC
hBwAwoQcAMKEHADChBwAwoQcAMKEHADChBwAwoQcAMKEHADChBwAwoQcAMKEHADChBwAwoQcAMKE
HADChBwAwoQcAMJ2F/ceLtMjAIAv4yMHgDAhB4AwIQeAMCEHgDAhB4AwIQeAMCEHgDAhB4AwIQeA
MCEHgDAhB4AwIQeAMCEHgDAhB4AwIQeAMCEHgDAhB4AwIQeAMCEHgDAhB4AwIQeAMCEHgDAhB4Aw
IQeAMCEHgDAhB4AwIQeAMCEHgDAhB4AwIQeAMCEHgDAhB4AwIQeAMCEHgDAhB4AwIQeAMCEHgDAh
B4AwIQeAMCEHgDAhB4AwIQeAMCEHgDAhB4AwIQeAMCEHgDAhB4AwIQeAMCEHgDAhB4AwIQeAMCEH
gDAhB4AwIQeAMCEHgDAhB4AwIQeAMCEHgDAhB4AwIQeAMCEHgDAhB4AwIQeAMCEHgDAhB4AwIQeA
MCEHgDAhB4AwIQeAMCEHgDAhB4AwIQeAMCEHgDAhB4AwIQeAMCEHgDAhB4AwIQeAMCEHgDAhB4Aw
IQeAMCEHgDAhB4AwIQeAMCEHgDAhB4AwIQeAMCEHgDAhB4AwIQeAsE+quElmTb4r0QAAAABJRU5E
rkJggg==
" transform="translate(22, 12)"/>
 
 
 
 
 
 
 
<image width="18" height="364" xlink:href="data:;base64,
iVBORw0KGgoAAAANSUhEUgAAABIAAAFsCAYAAADBkelSAAACHUlEQVR4nO2c223EMAwEqUD9V5Eu
4yOvBPpjEAwIqoCF9kU5vljnyd8KYP0QIBERN+thgAoC4qhVzqVmcw0Te7BGHLWgkk0BgdQo1yZr
lH8Q0Ca7Wxy1Ux8GKBICOhAQaT+lESQ2aD9Gbe1vgU4mAiSkRgEpk824NjnZRvsh1yj7la6N1Qi0
35ZsnWtC+yORF1pxo3zUMNcYjZTUVqMeCMFBqUFAUGeN1HRA5Ds2CKjyIEBK+xlqt8qnEUSNAiLf
+Y+lFslgTdaImkc3itmUkJpxZm+ym3XLppHwOKI0Eh5HXPt1gw2035Zs0P6x7QeT7aO2rrVAtooY
2++z33aukf8PKSutUKNN9j8C5WrUraXWL18gZ2s09mlk8DzaZPdAQvtDRk1oP/TjupMaZT+Uo8Gl
NdpPAQmpYa7pks2VFhtsOo249iMwS+3NMs5sBEbZ/qXWA/ke2AfPbIya8WEUAtJVZO3vF2g/g6Oc
2XM1AqnZkg0eRxAQtSOlRmt/s4TUVqMXQAyOcmbr5pFu1N6CPqoRJntwaXU5MrZfl+zB1MCfM6Dv
sn3n2s7sF0A6apTYGDWhRkmVVpjswa5R1Ar6etmo0cGo2a4JoXYE2n909nPJttkPltZ2/xGYbOge
LZ/9Oo2WWr/A0kI34GA7Iv/KnksNm0eDNeKo6dq/rvVAVEWoHQmHf+kumcaoBfQmArwngnON0sjX
fs7+udQgoC/rNOfnsknqIwAAAABJRU5ErkJggg==
" transform="translate(532, 12)"/>
 
 
 - 
 
 
 10.0 
 
 
 - 
 
 
 7.5 
 
 
 - 
 
 
 5.0 
 
 
 - 
 
 
 2.5 
 
 
 0 
 
 
 2.5 
 
 
 5.0 
 
 
 7.5 
 
 
 10.0 
 
<polyline clip-path="url(#clip5100)" style="stroke:#000000; stroke-width:1; stroke-opacity:1; fill:none" points="
 550.315,375.813 550.315,359.268 556.315,359.268 550.31

min torque = -11.0
max torque = 11.0
Value function for the 2 link acrobot in unstable equilibrium:


<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 -10 
 
 
 -5 
 
 
 0 
 
 
 5 
 
 
 10 
 
 
 -10 
 
 
 -5 
 
 
 0 
 
 
 5 
 
 
 10 
 
 
<image width="484" height="364" xlink:href="data:;base64,
iVBORw0KGgoAAAANSUhEUgAAAeQAAAFsCAYAAAAdTcpMAAAHdklEQVR4nO3XW26VZRiG4bVgAaUg
VBpDEI3xQI/czcA4GA8cgVM08cgYB2AMbtmJUGtpXY7hO3rvxusawZM/X/4773az2e03AMCoK9MD
AABBBoAEQQaAAEEGgABBBoAAQQaAAEEGgABBBoAAQQaAAEEGgABBBoAAQQaAAEEGgABBBoAAQQaA
AEEGgABBBoAAQQaAAEEGgABBBoAAQQaAAEEGgABBBoAAQQaAAEEGgABBBoAAQQaAAEEGgABBBoAA
QQaAAEEGgABBBoAAQQaAAEEGgABBBoAAQQaAAEEGgABBBoAAQQaAAEEGgABBBoAAQQaAAEEGgABB
BoAAQQaAAEEGgABBBoAAQQaAAEEGgABBBoAAQQaAAEEGgABBBoAAQQaAAEEGgABBBoAAQQaAAEEG
gABBBoAAQQaAAEEGgABBBoAAQQaAAEEGgABBBoAAQQaAgN2dgw+nNyw5PX86PWHJ2fnj6QkAXAIu
ZAAIEGQACBBkAAgQZAAIEGQACBBkAAgQZAAIEGQACBBkAAgQZAAIEGQACBBkAAgQZAAIEGQACBBk
AAgQZAAIEGQACBBkAAgQZAAIEGQACBBkAAgQZAAIEGQACBBkAAgQZAAIEGQACBBkAAgQZAAIEGQA
CBBkAAgQZAAIEGQACNh9/eCL6Q1L/ji9Oj1hyaOT/fSEJb++Pp2esOTJ9vn0hCXPt79PT1jy6uLx
9IQlp+eX6z2cX7ycnrDk3/3l+j/s9xfTE5a4kAEgQJABIECQASBAkAEgQJABIECQASBAkAEgQJAB
IECQASBAkAEgQJABIECQASBAkAEgQJABIECQASBAkAEgQJABIECQASBAkAEgQJABIECQASBAkAEg
QJABIECQASBAkAEgQJABIECQASBAkAEgQJABIECQASBAkAEgQJABIGD75KsP9tMjVuwOzqYnLLl4
vZuesOTs5eH0hCV/PbszPWHJ0+dH0xOW/PLicu39+eTW9IQlj05uTE9Y8tPJdnrCkh//Pp2esMSF
DAABggwAAYIMAAGCDAABggwAAYIMAAGCDAABggwAAYIMAAGCDAABggwAAYIMAAGCDAABggwAAYIM
AAGCDAABggwAAYIMAAGCDAABggwAAYIMAAGCDAABggwAAYIMAAGCDAABggwAAYIMAAGCDAABggwA
AYIMAAGCDAABggwAAbvpAatuffbb9IQl5x99Oj1hybW3P56esOTuvU+mJyx5//q96QlLXp89nZ6w
5PzZ99MTllx79O30hCW7H76bnrDkz28eTk9Y4kIGgABBBoAAQQaAAEEGgABBBoAAQQaAAEEGgABB
BoAAQQaAAEEGgABBBoAAQQaAAEEGgABBBoAAQQaAAEEGgABBBoAAQQaAAEEGgABBBoAAQQaAAEEG
gABBBoAAQQaAAEEGgABBBoAAQQaAAEEGgABBBoAAQQaAAEEGgABBBoCA7eeHX+6nR6x47+Dm9IQl
7966VJ938/Dwn+kJSx4cvpqesOTBnefTE5YcH12uvbfffDE9YcmN2yfTE5Zc2Z1PT1hycXZ9esIS
FzIABAgyAAQIMgAECDIABAgyAAQIMgAECDIABAgyAAQIMgAECDIABAgyAAQIMgAECDIABAgyAAQI
MgAECDIABAgyAAQIMgAECDIABAgyAAQIMgAECDIABAgyAAQIMgAECDIABAgyAAQIMgAECDIABAgy
AAQIMgAECDIABAgyAARsN5vdfnrEiu326vSEJVe2N6YnLNldfWN6wpKD3dH0hCW3rh5PT1hytL8/
PWHJ8f7u9IQl96/dnJ6w5J3D7fSEJW8dXExPWOJCBoAAQQaAAEEGgABBBoAAQQaAAEEGgABBBoAA
QQaAAEEGgABBBoAAQQaAAEEGgABBBoAAQQaAAEEGgABBBoAAQQaAAEEGgABBBoAAQQaAAEEGgABB
BoAAQQaAAEEGgABBBoAAQQaAAEEGgABBBoAAQQaAAEEGgABBBoAAQQaAgO1ms9tPjwCg7/rueHrC
khu7e9MTlriQASBAkAEgQJABIECQASBAkAEgQJABIECQASBAkAEgQJABIECQASBAkAEgQJABIECQ
ASBAkAEgQJABIECQASBAkAEgQJABIECQASBAkAEgQJABIECQASBAkAEgQJABIECQASBAkAEgQJAB
IECQASBAkAEgQJABIECQASBAkAEgYLvZ7PbTIwDg/86FDAABggwAAYIMAAGCDAABggwAAYIMAAGC
DAABggwAAYIMAAGCDAABggwAAYIMAAGCDAABggwAAYIMAAGCDAABggwAAYIMAAGCDAABggwAAYIM
AAGCDAABggwAAYIMAAGCDAABggwAAYIMAAGCDAABggwAAYIMAAGCDAABggwAAYIMAAGCDAABggwA
AYIMAAGCDAABggwAAYIMAAGCDAABggwAAYIMAAGCDAABggwAAYIMAAGCDAABggwAAYIMAAGCDAAB
ggwAAYIMAAGCDAABggwAAYIMAAGCDAABggwAAYIMAAGCDAABggwAAYIMAAGCDAABggwAAYIMAAGC
DAABggwAAf8B2YVcPOn3tXQAAAAASUVORK5CYII=
" transform="translate(36, 12)"/>
 
 
 
 
 
 
 
<image width="18" height="364" xlink:href="data:;base64,
iVBORw0KGgoAAAANSUhEUgAAABIAAAFsCAYAAADBkelSAAACHUlEQVR4nO2c223EMAwEqUD9V5Eu
4yOvBPpjEAwIqoCF9kU5vljnyd8KYP0QIBERN+thgAoC4qhVzqVmcw0Te7BGHLWgkk0BgdQo1yZr
lH8Q0Ca7Wxy1Ux8GKBICOhAQaT+lESQ2aD9Gbe1vgU4mAiSkRgEpk824NjnZRvsh1yj7la6N1Qi0
35ZsnWtC+yORF1pxo3zUMNcYjZTUVqMeCMFBqUFAUGeN1HRA5Ds2CKjyIEBK+xlqt8qnEUSNAiLf
+Y+lFslgTdaImkc3itmUkJpxZm+ym3XLppHwOKI0Eh5HXPt1gw2035Zs0P6x7QeT7aO2rrVAtooY
2++z33aukf8PKSutUKNN9j8C5WrUraXWL18gZ2s09mlk8DzaZPdAQvtDRk1oP/TjupMaZT+Uo8Gl
NdpPAQmpYa7pks2VFhtsOo249iMwS+3NMs5sBEbZ/qXWA/ke2AfPbIya8WEUAtJVZO3vF2g/g6Oc
2XM1AqnZkg0eRxAQtSOlRmt/s4TUVqMXQAyOcmbr5pFu1N6CPqoRJntwaXU5MrZfl+zB1MCfM6Dv
sn3n2s7sF0A6apTYGDWhRkmVVpjswa5R1Ar6etmo0cGo2a4JoXYE2n909nPJttkPltZ2/xGYbOge
LZ/9Oo2WWr/A0kI34GA7Iv/KnksNm0eDNeKo6dq/rvVAVEWoHQmHf+kumcaoBfQmArwngnON0sjX
fs7+udQgoC/rNOfnsknqIwAAAABJRU5ErkJggg==
" transform="translate(532, 12)"/>
 
 
 500 
 
 
 1000 
 
 
 1500 
 
 
 2000 
 
 
 2500 
 
 
 3000 
 
 
 3500 
 
 
 4000 
 
<polyline clip-path="url(#clip5300

min value = 30.0
max value = 4184.150797027355
Policy for the 2 link acrobot  in unstable equilibrium:


<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 -10 
 
 
 -5 
 
 
 0 
 
 
 5 
 
 
 10 
 
 
 -10 
 
 
 -5 
 
 
 0 
 
 
 5 
 
 
 10 
 
 
<image width="484" height="364" xlink:href="data:;base64,
iVBORw0KGgoAAAANSUhEUgAAAeQAAAFsCAYAAAAdTcpMAAAGn0lEQVR4nO3XMWpUARiFUSMDNroI
QbeQpLVIZSEp3FeWkCI2NmHqKQLaGNNYWQnZRMoJ4xoeDPxfHues4HYf92R39vXwCgAY9Xp6AAAg
yACQIMgAECDIABAgyAAQIMgAECDIABAgyAAQIMgAECDIABAgyAAQIMgAECDIABAgyAAQIMgAECDI
ABAgyAAQIMgAECDIABAgyAAQIMgAECDIABAgyAAQIMgAECDIABAgyAAQIMgAECDIABAgyAAQIMgA
ECDIABAgyAAQIMgAECDIABAgyAAQIMgAECDIABAgyAAQIMgAECDIABAgyAAQIMgAECDIABAgyAAQ
IMgAECDIABAgyAAQIMgAECDIABAgyAAQIMgAECDIABAgyAAQIMgAECDIABAgyAAQIMgAECDIABAg
yAAQIMgAECDIABAgyAAQIMgAECDIABAgyAAQIMgAELCZHrDUxf3t9IRFdmeX0xMAeAE8ZAAIEGQA
CBBkAAgQZAAIEGQACBBkAAgQZAAIEGQACBBkAAgQZAAIEGQACBBkAAgQZAAIEGQACBBkAAgQZAAI
EGQACBBkAAgQZAAIEGQACBBkAAgQZAAIEGQACBBkAAgQZAAIEGQACBBkAAgQZAAIEGQACBBkAAgQ
ZAAIEGQACNhMD1i7i/vb6QmL7A/X0xMAjuLufDs9YREPGQACBBkAAgQZAAIEGQACBBkAAgQZAAIE
GQACBBkAAgQZAAIEGQACBBkAAgQZAAIEGQACBBkAAgQZAAIEGQACBBkAAgQZAAIEGQACBBkAAgQZ
AAIEGQACBBkAAgQZAAIEGQACBBkAAgQZAAIEGQACBBkAAgQZAAIEGQACBBkAAk72h5vD9AiAY/j4
7tv0hFV7fNpNT1g1DxkAAgQZAAIEGQACBBkAAgQZAAIEGQACBBkAAgQZAAIEGQACBBkAAgQZAAIE
GQACBBkAAgQZAAIEGQACBBkAAgQZAAIEGQACBBkAAgQZAAIEGQACBBkAAgQZAAIEGQACBBkAAgQZ
AAIEGQACBBkAAgQZAAIEGQACBBkAAgQZAAI20wOWen64mp6wbj//Ti9Y5Mf3z9MTCDndfJiesMjv
/b/pCYu8f3sxPWGRx6fd9IRFPGQACBBkAAgQZAAIEGQACBBkAAgQZAAIEGQACBBkAAgQZAAIEGQA
CBBkAAgQZAAIEGQACBBkAAgQZAAIEGQACBBkAAgQZAAIEGQACBBkAAgQZAAIEGQACBBkAAgQZAAI
EGQACBBkAAgQZAAIEGQACBBkAAgQZAAIEGQACBBkAAg42R9uDtMj1uz54Wp6wqq9Of0zPQHgKDxk
AAgQZAAIEGQACBBkAAgQZAAIEGQACBBkAAgQZAAIEGQACBBkAAgQZAAIEGQACBBkAAgQZAAIEGQA
CBBkAAgQZAAIEGQACBBkAAgQZAAIEGQACBBkAAgQZAAIEGQACBBkAAgQZAAIEGQACBBkAAgQZAAI
EGQACBBkAAgQZAAI2Nydb6c3LHJxfzs9AeAo9ofr6Qmr9tL65iEDQIAgA0CAIANAgCADQIAgA0CA
IANAgCADQIAgA0CAIANAgCADQIAgA0CAIANAgCADQIAgA0CAIANAgCADQIAgA0CAIANAgCADQIAg
A0CAIANAgCADQIAgA0CAIANAgCADQIAgA0CAIANAgCADQIAgA0CAIANAgCADQIAgA0DAZnrAUruz
y+kJAEdxd76dnrDIp19fpiesmocMAAGCDAABggwAAYIMAAGCDAABggwAAYIMAAGCDAABggwAAYIM
AAGCDAABggwAAYIMAAGCDAABggwAAYIMAAGCDAABggwAAYIMAAGCDAABggwAAYIMAAGCDAABggwA
AYIMAAGCDAABggwAAYIMAAGCDAABggwAAYIMAAGCDAABm+kBALwMd+fb6Qmr5iEDQIAgA0CAIANA
gCADQIAgA0CAIANAgCADQIAgA0CAIANAgCADQIAgA0CAIANAgCADQIAgA0CAIANAgCADQIAgA0CA
IANAgCADQIAgA0CAIANAgCADQIAgA0CAIANAgCADQIAgA0CAIANAgCADQIAgA0CAIANAgCADQIAg
A0CAIANAgCADQIAgA0CAIANAgCADQIAgA0CAIANAgCADQIAgA0CAIANAgCADQIAgA0CAIANAgCAD
QIAgA0CAIANAgCADQIAgA0CAIANAgCADQIAgA0CAIANAgCADQIAgA0CAIANAgCADQIAgA0CAIANA
gCADQIAgA0CAIANAgCADQIAgA0DAfxEjNWm0bJgGAAAAAElFTkSuQmCC
" transform="translate(36, 12)"/>
 
 
 
 
 
 
 
<image width="18" height="364" xlink:href="data:;base64,
iVBORw0KGgoAAAANSUhEUgAAABIAAAFsCAYAAADBkelSAAACHUlEQVR4nO2c223EMAwEqUD9V5Eu
4yOvBPpjEAwIqoCF9kU5vljnyd8KYP0QIBERN+thgAoC4qhVzqVmcw0Te7BGHLWgkk0BgdQo1yZr
lH8Q0Ca7Wxy1Ux8GKBICOhAQaT+lESQ2aD9Gbe1vgU4mAiSkRgEpk824NjnZRvsh1yj7la6N1Qi0
35ZsnWtC+yORF1pxo3zUMNcYjZTUVqMeCMFBqUFAUGeN1HRA5Ds2CKjyIEBK+xlqt8qnEUSNAiLf
+Y+lFslgTdaImkc3itmUkJpxZm+ym3XLppHwOKI0Eh5HXPt1gw2035Zs0P6x7QeT7aO2rrVAtooY
2++z33aukf8PKSutUKNN9j8C5WrUraXWL18gZ2s09mlk8DzaZPdAQvtDRk1oP/TjupMaZT+Uo8Gl
NdpPAQmpYa7pks2VFhtsOo249iMwS+3NMs5sBEbZ/qXWA/ke2AfPbIya8WEUAtJVZO3vF2g/g6Oc
2XM1AqnZkg0eRxAQtSOlRmt/s4TUVqMXQAyOcmbr5pFu1N6CPqoRJntwaXU5MrZfl+zB1MCfM6Dv
sn3n2s7sF0A6apTYGDWhRkmVVpjswa5R1Ar6etmo0cGo2a4JoXYE2n909nPJttkPltZ2/xGYbOge
LZ/9Oo2WWr/A0kI34GA7Iv/KnksNm0eDNeKo6dq/rvVAVEWoHQmHf+kumcaoBfQmArwngnON0sjX
fs7+udQgoC/rNOfnsknqIwAAAABJRU5ErkJggg==
" transform="translate(532, 12)"/>
 
 
 - 
 
 
 10.0 
 
 
 - 
 
 
 7.5 
 
 
 - 
 
 
 5.0 
 
 
 - 
 
 
 2.5 
 
 
 0 
 
 
 2.5 
 
 
 5.0 
 
 
 7.5 
 
 
 10.0 
 
<polyline clip-path="url(#clip5500)" style="stroke:#000000; stroke-width:1; stroke-opacity:1; fill:none" points="
 550.315,375.813 550.315,359.268 556.315,359.268 550.315,359.268 550.315,317.904 556.315,317.904 550.315,317.904 550.315,276.54 556.315,276.54 550.315,276.54 
 550.315,235.176 5

min torque = -11.0
max torque = 11.0


Finally the animation should indicate if we have ultimately succeeded:

In [261]:
anim(init_vertical_perturbed(Val{2}), sim2, get_optimal_policy(vi2), advance, "discrete_vi_acrobot_simple10", 2000)

Unfortunately the result doesn't maintain the unstable equilibrium, but swings between them. This is more representative of the swing-up strategy than a balancing solution.

Perhaps the simulation above lacks resolution. Let's repeat the processes at a higher resolution:

In [248]:
@time vi3, sim3 = begin
    vi = ValueIteration{4}(StateGrid(;nθs=18,nωs=11,nτs=9,ω_lim=11.0,τ_lim=11.0), γ=0.99, bdry_penalty=-5)
    init(vi)
    sim = Simulation{2}(ACROBOT)
    train_vi(vi, sim);
    print("The state space is discretized into a finite number ");
    println("of angles, angular velocities and torques as follows")
    println("θ = ", θ.(vi.grid, 1:vi.grid.nθs))
    println("ω = ", ω.(vi.grid, 1:vi.grid.nωs))
    println("τ = ", τ.(vi.grid, 1:vi.grid.nτs))
    vi, sim
end;

Progress: ==================================================> 100%; residual = 1.0117976765134426e-5   
final residual = 9.881345919553079e-6
The state space is discretized into a finite number of angles, angular velocities and torques as follows
θ = [0.392699, 0.785398, 1.1781, 1.5708, 1.9635, 2.35619, 2.74889, 3.14159, 3.53429, 3.92699, 4.31969, 4.71239, 5.10509, 5.49779, 5.89049, 6.28319]
ω = [-11.0, -8.8, -6.6, -4.4, -2.2, 0.0, 2.2, 4.4, 6.6, 8.8, 11.0]
τ = [-11.0, -8.25, -5.5, -2.75, 0.0, 2.75, 5.5, 8.25, 11.0]
3404.823509 seconds (4.01 M allocations: 566.550 MiB, 0.01% gc time)


In [272]:
show_solution(vi3, sim3) # Recall that θ₁ and ω₁ are on the y axis

Value function for the 2 link acrobot at zero angular velocity:


<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 1 
 
 
 2 
 
 
 3 
 
 
 4 
 
 
 5 
 
 
 6 
 
 
 1 
 
 
 2 
 
 
 3 
 
 
 4 
 
 
 5 
 
 
 6 
 
 
<image width="364" height="364" xlink:href="data:;base64,
iVBORw0KGgoAAAANSUhEUgAAAWwAAAFsCAYAAADon4O5AAAHwklEQVR4nO3d226cZxmG4W8cu3ac
Jk2MLTdVq6gqYgsJ2OBo2OAAkDg2zgTELgsFUKCmVlbOwokXwykg8Vb0lq7rAB7NL83c8++9m7V2
twuAH7yd//cHAOC/I9gAEYINECHYABGCDRAh2AARgg0QIdgAEYINECHYABGCDRAh2AARgg0QIdgA
EYINECHYABGCDRAh2AARgg0QIdgAEYINECHYABGCDRAh2AARgg0QIdgAEYINECHYABGCDRAh2AAR
gg0QIdgAEYINECHYABGCDRAh2AARgg0QIdgAEYINECHYABGCDRAh2AARgg0QIdgAEYINECHYABGC
DRAh2AARgg0QIdgAEYINECHYABGCDRAh2AARgg0QIdgAEYINECHYABGCDRAh2AARgg0QIdgAEYIN
ECHYABGCDRAh2AARgg0QIdgAEYINECHYABGCDRAh2AARgg0QIdgAEYINECHYABGCDRAh2AARgg0Q
IdgAEYINECHYABGCDRAh2AARgg0QIdgAEYINECHYABGCDRAh2AARgg0QIdgAEYINECHYABGCDRAh
2AARgg0QIdgAEYINECHYABGCDRAh2AARgg0QIdgAEYINECHYABGCDRAh2AARgg0QIdgAEYINECHY
ABGCDRAh2AARgg0QIdgAEYINECHYABGCDRAh2AARgg0Qsft9jO5sPhnd273zYHTv7t7x6N6DO6ej
e2utdX97NLp3b3s4ure2m9G5tztvR/debM5G99Za6+L629G9y6vz0b3rm9eje/zweMMGiBBsgAjB
BogQbIAIwQaIEGyACMEGiBBsgAjBBogQbIAIwQaIEGyACMEGiBBsgAjBBogQbIAIwQaIEGyACMEG
iNj88vDX2+nRo8290b3HB7OnJ784nH3k04Or0b211jo5uBzdu//Jh9G9m9vZ//rvLu+O7v3z3cHo
3lprPXs3/Mwfbmf3rme/M3/beTq6t9Zab25n71ju79wf3Xu4PRneezi65w0bIEKwASIEGyBCsAEi
BBsgQrABIgQbIEKwASIEGyBCsAEiBBsgQrABIgQbIEKwASIEGyBCsAEiBBsgQrABIgQbIGLzu1/8
avym45cPn4/uHR29GN17cDy7d++rs9G9tdbae/JxdG/76LPRvc2796N72xez9wg/PJ29pbfWWi//
/nh07/zfx6N7f/nudHTv6cXsvcS11vowfAv0093r2b292b3jg9nfiTdsgAjBBogQbIAIwQaIEGyA
CMEGiBBsgAjBBogQbIAIwQaIEGyACMEGiBBsgAjBBogQbIAIwQaIEGyACMEGiBBsgIjdH5/+a3x0
b+9qdO/m+s7o3sf3+6N7926+h/+9zz4dnbv65qeje9enPxvdO3z089G92xd/GN1ba62jsz+O7n3+
p9nP+JPfz94jfPnnr0b31lrrzavZO5E3N7Nt+PBxtg27u7Mt9IYNECHYABGCDRAh2AARgg0QIdgA
EYINECHYABGCDRAh2AARgg0QIdgAEYINECHYABGCDRAh2AARgg0QIdgAEYINECHYABGb35z+djs9
eju8dzh7Z3M9vjt7GPPr+xeje2ut9c3J2eje8cn56N7DJ7PHm/efvBzd2xwdjO6ttdb28O7o3ubF
q9G9q7/OPvPFP05H99Za6/X5o9G95y8fju49ezX7+c7fH47uecMGiBBsgAjBBogQbIAIwQaIEGyA
CMEGiBBsgAjBBogQbIAIwQaIEGyACMEGiBBsgAjBBogQbIAIwQaIEGyACMEGiNjsbA7HbzpuNruj
e/t7x6N7P9r7enTvye3s3lprnezO3uc73p/9b/7ycPZy5xeHl6N7JwfvR/fWWuvOzuwzX3zcH937
7nL2O3N2uTe6t9Zaz95tRve+vbwe3Xu+fTu6d7F5M7rnDRsgQrABIgQbIEKwASIEGyBCsAEiBBsg
QrABIgQbIEKwASIEGyBCsAEiBBsgQrABIgQbIEKwASIEGyBCsAEiBBsgYrPW7vhNR/53u3cejO4d
DN/FvL/7+ejeo+3p6N6923uje2uttTazP5W3m3ejexeb56N7r2/ORvfWWuv91fno3vXN69G92+3H
0b1p3rABIgQbIEKwASIEGyBCsAEiBBsgQrABIgQbIEKwASIEGyBCsAEiBBsgQrABIgQbIEKwASIE
GyBCsAEiBBsgQrABItx0BIjwhg0QIdgAEYINECHYABGCDRAh2AARgg0QIdgAEYINECHYABGCDRAh
2AARgg0QIdgAEYINECHYABGCDRAh2AARgg0QIdgAEYINECHYABGCDRAh2AARgg0QIdgAEYINECHY
ABGCDRAh2AARgg0QIdgAEYINECHYABGCDRAh2AARgg0QIdgAEYINECHYABGCDRAh2AARgg0QIdgA
EYINECHYABGCDRAh2AARgg0QIdgAEYINECHYABGCDRAh2AARgg0QIdgAEYINECHYABGCDRAh2AAR
gg0QIdgAEYINECHYABGCDRAh2AARgg0QIdgAEYINECHYABGCDRAh2AARgg0QIdgAEYINECHYABGC
DRAh2AARgg0QIdgAEYINECHYABGCDRAh2AARgg0QIdgAEYINECHYABGCDRAh2AARgg0QIdgAEYIN
ECHYABGCDRAh2AARgg0QIdgAEYINECHYABH/AUwoqZUf1XnxAAAAAElFTkSuQmCC
" transform="translate(89, 12)"/>
 
 
 
 
 
 
 
<image width="18" height="364" xlink:href="data:;base64,
iVBORw0KGgoAAAANSUhEUgAAABIAAAFsCAYAAADBkelSAAACHUlEQVR4nO2c223EMAwEqUD9V5Eu
4yOvBPpjEAwIqoCF9kU5vljnyd8KYP0QIBERN+thgAoC4qhVzqVmcw0Te7BGHLWgkk0BgdQo1yZr
lH8Q0Ca7Wxy1Ux8GKBICOhAQaT+lESQ2aD9Gbe1vgU4mAiSkRgEpk824NjnZRvsh1yj7la6N1Qi0
35ZsnWtC+yORF1pxo3zUMNcYjZTUVqMeCMFBqUFAUGeN1HRA5Ds2CKjyIEBK+xlqt8qnEUSNAiLf
+Y+lFslgTdaImkc3itmUkJpxZm+ym3XLppHwOKI0Eh5HXPt1gw2035Zs0P6x7QeT7aO2rrVAtooY
2++z33aukf8PKSutUKNN9j8C5WrUraXWL18gZ2s09mlk8DzaZPdAQvtDRk1oP/TjupMaZT+Uo8Gl
NdpPAQmpYa7pks2VFhtsOo249iMwS+3NMs5sBEbZ/qXWA/ke2AfPbIya8WEUAtJVZO3vF2g/g6Oc
2XM1AqnZkg0eRxAQtSOlRmt/s4TUVqMXQAyOcmbr5pFu1N6CPqoRJntwaXU5MrZfl+zB1MCfM6Dv
sn3n2s7sF0A6apTYGDWhRkmVVpjswa5R1Ar6etmo0cGo2a4JoXYE2n909nPJttkPltZ2/xGYbOge
LZ/9Oo2WWr/A0kI34GA7Iv/KnksNm0eDNeKo6dq/rvVAVEWoHQmHf+kumcaoBfQmArwngnON0sjX
fs7+udQgoC/rNOfnsknqIwAAAABJRU5ErkJggg==
" transform="translate(465, 12)"/>
 
 
 5

min value = 5.0
max value = 3218.380280997004
Policy for the 2 link acrobot at zero angular velocity:


<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 1 
 
 
 2 
 
 
 3 
 
 
 4 
 
 
 5 
 
 
 6 
 
 
 1 
 
 
 2 
 
 
 3 
 
 
 4 
 
 
 5 
 
 
 6 
 
 
<image width="364" height="364" xlink:href="data:;base64,
iVBORw0KGgoAAAANSUhEUgAAAWwAAAFsCAYAAADon4O5AAAGM0lEQVR4nO3dIW5UYRhGYYZOULVI
RINhATSDRVQ3FfgqNDtgBZQ6LK6LGE+AQkhQKOpLgsKQMAwCXwj87e1pn2cBbz4xc3LdP1suHq1v
AHDp3Zz6AAD+jmADRAg2QIRgA0QINkCEYANECDZAhGADRAg2QIRgA0QINkCEYANECDZAhGADRAg2
QIRgA0QINkCEYANECDZAhGADRAg2QIRgA0QINkCEYANECDZAhGADRAg2QIRgA0QINkCEYANECDZA
hGADRAg2QIRgA0QINkCEYANECDZAhGADRAg2QIRgA0QINkCEYANECDZAhGADRAg2QIRgA0QINkCE
YANECDZAhGADRAg2QIRgA0QINkCEYANECDZAhGADRAg2QIRgA0QINkCEYANECDZAhGADRAg2QIRg
A0QINkCEYANECDZAhGADRAg2QIRgA0QINkCEYANECDZAhGADRAg2QIRgA0QINkCEYANECDZAhGAD
RAg2QIRgA0QINkCEYANECDZAhGADRAg2QIRgA0QINkCEYANECDZAhGADRAg2QIRgA0QINkCEYANE
CDZAhGADRAg2QIRgA0QINkCEYANECDZAhGADRAg2QIRgA0QINkCEYANECDZAhGADRAg2QIRgA0QI
NkCEYANECDZAhGADRAg2QIRgA0QINkCEYANECDZAxPw8Rh++3h26tzo+HLq3sf1k6F7BfLY/9Ql5
W5s7U59wppNvy6F7y8Xe0D3+ny9sgAjBBogQbIAIwQaIEGyACMEGiBBsgAjBBogQbIAIwQaIEGyA
CMEGiBBsgAjBBogQbIAIwQaIEGyACMEGiBBsgIjZ97f311Mf8SfX8Q3G62Z18Hjo3um7e0P3zsOd
o49Tn3DhfqxfTn1Cmi9sgAjBBogQbIAIwQaIEGyACMEGiBBsgAjBBogQbIAIwQaIEGyACMEGiBBs
gAjBBogQbIAIwQaIEGyACMEGiBBsgIj5eYx6g/HqWx0fDt3zBiNX0ej/iS9sgAjBBogQbIAIwQaI
EGyACMEGiBBsgAjBBogQbIAIwQaIEGyACMEGiBBsgAjBBogQbIAIwQaIEGyACMEGiBBsgIi59xf5
F6fPfw7d+/T57tC9D19uD937zZuO/2s+25/6hAv1/dmtoXu+sAEiBBsgQrABIgQbIEKwASIEGyBC
sAEiBBsgQrABIgQbIEKwASIEGyBCsAEiBBsgQrABIgQbIEKwASIEGyBCsAEiBBsgYj71ATQdvXkw
9QlnenF6MvUJBG1t7gzdu/d06JwvbIAKwQaIEGyACMEGiBBsgAjBBogQbIAIwQaIEGyACMEGiBBs
gAjBBogQbIAIwQaIEGyACMEGiBBsgAjBBogQbIAIbzpeEwd3X019wpnef90YunfybTl0j8tp9BuM
o43+HfrCBogQbIAIwQaIEGyACMEGiBBsgAjBBogQbIAIwQaIEGyACMEGiBBsgAjBBogQbIAIwQaI
EGyACMEGiBBsgAjBBoiYLReP1lMfUffw9e7wzdXx4fDNkTa2n0x9Qt58tj/1CRdu9BuMo99MXC72
hu6N5gsbIEKwASIEGyBCsAEiBBsgQrABIgQbIEKwASIEGyBCsAEiBBsgQrABIgQbIEKwASIEGyBC
sAEiBBsgQrABIgQbIMKbjgARvrABIgQbIEKwASIEGyBCsAEiBBsgQrABIgQbIEKwASIEGyBCsAEi
BBsgQrABIgQbIEKwASIEGyBCsAEiBBsgQrABIgQbIEKwASIEGyBCsAEiBBsgQrABIgQbIEKwASIE
GyBCsAEiBBsgQrABIgQbIEKwASIEGyBCsAEiBBsgQrABIgQbIEKwASIEGyBCsAEiBBsgQrABIgQb
IEKwASIEGyBCsAEiBBsgQrABIgQbIEKwASIEGyBCsAEiBBsgQrABIgQbIEKwASIEGyBCsAEiBBsg
QrABIgQbIEKwASIEGyBCsAEiBBsgQrABIgQbIEKwASIEGyBCsAEiBBsgQrABIgQbIEKwASIEGyBC
sAEiBBsgQrABIgQbIEKwASIEGyBCsAEiBBsgQrABIgQbIEKwASIEGyBCsAEiBBsgQrABIgQbIEKw
ASIEGyBCsAEiBBsgQrABIgQbIEKwASIEGyDiFxO1R4l9Zv4zAAAAAElFTkSuQmCC
" transform="translate(89, 12)"/>
 
 
 
 
 
 
 
<image width="18" height="364" xlink:href="data:;base64,
iVBORw0KGgoAAAANSUhEUgAAABIAAAFsCAYAAADBkelSAAACHUlEQVR4nO2c223EMAwEqUD9V5Eu
4yOvBPpjEAwIqoCF9kU5vljnyd8KYP0QIBERN+thgAoC4qhVzqVmcw0Te7BGHLWgkk0BgdQo1yZr
lH8Q0Ca7Wxy1Ux8GKBICOhAQaT+lESQ2aD9Gbe1vgU4mAiSkRgEpk824NjnZRvsh1yj7la6N1Qi0
35ZsnWtC+yORF1pxo3zUMNcYjZTUVqMeCMFBqUFAUGeN1HRA5Ds2CKjyIEBK+xlqt8qnEUSNAiLf
+Y+lFslgTdaImkc3itmUkJpxZm+ym3XLppHwOKI0Eh5HXPt1gw2035Zs0P6x7QeT7aO2rrVAtooY
2++z33aukf8PKSutUKNN9j8C5WrUraXWL18gZ2s09mlk8DzaZPdAQvtDRk1oP/TjupMaZT+Uo8Gl
NdpPAQmpYa7pks2VFhtsOo249iMwS+3NMs5sBEbZ/qXWA/ke2AfPbIya8WEUAtJVZO3vF2g/g6Oc
2XM1AqnZkg0eRxAQtSOlRmt/s4TUVqMXQAyOcmbr5pFu1N6CPqoRJntwaXU5MrZfl+zB1MCfM6Dv
sn3n2s7sF0A6apTYGDWhRkmVVpjswa5R1Ar6etmo0cGo2a4JoXYE2n909nPJttkPltZ2/xGYbOge
LZ/9Oo2WWr/A0kI34GA7Iv/KnksNm0eDNeKo6dq/rvVAVEWoHQmHf+kumcaoBfQmArwngnON0sjX
fs7+udQgoC/rNOfnsknqIwAAAABJRU5ErkJggg==
" transform="translate(465, 12)"/>
 
 
 - 
 
 
 10.0 
 
 
 - 
 
 
 7.5 
 
 
 - 
 
 
 5.0 
 
 
 - 
 
 
 2.5 
 
 
 0 
 
 
 2.5 
 
 
 5.0 
 
 
 7.5 
 
 
 10.0 
 
<polyline clip-path="url(#clip6300)" style="stroke:#000000; stroke-width:1; stroke-opacity:1; fill:none" points="
 483.328,375.813 483.328,359.268 489.328,359.268 483.328,359.268 483.328,317.904 489.328,317.904 483.328,317.904 483.328,276.54 489.328,276.54 483.328,276.54 
 483.328,235.176 489.328,235.176 483.328,235.176 483.328,193.812 489.328,193.812 483.328,193.812 483.328,152.448 489.328,152.448 483.328,152.448 483

min torque = -11.0
max torque = 11.0
Value function for the 2 link acrobot in unstable equilibrium:


<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 -10 
 
 
 -5 
 
 
 0 
 
 
 5 
 
 
 10 
 
 
 -10 
 
 
 -5 
 
 
 0 
 
 
 5 
 
 
 10 
 
 
<image width="364" height="364" xlink:href="data:;base64,
iVBORw0KGgoAAAANSUhEUgAAAWwAAAFsCAYAAADon4O5AAAGaUlEQVR4nO3WwYoVdBiH4e8cR/OM
qRiRUKIQtKpVUnQDdQ/dQpfZKoIWLcJFEDVUSFCR5hxN55wuoXb/eeF5ruC3er9vM3NyHAAuve3q
AQD8P4INECHYABGCDRAh2AARgg0QIdgAEYINECHYABGCDRAh2AARgg0QIdgAEYINECHYABGCDRAh
2AARgg0QIdgAEYINECHYABGCDRAh2AARgg0QIdgAEYINECHYABGCDRAh2AARgg0QIdgAEYINECHY
ABGCDRAh2AARgg0QIdgAEYINECHYABGCDRAh2AARgg0QIdgAEYINECHYABGCDRAh2AARgg0QIdgA
EYINECHYABGCDRAh2AARgg0QIdgAEYINECHYABGCDRAh2AARgg0QIdgAEYINECHYABGCDRAh2AAR
gg0QIdgAEYINECHYABGCDRAh2AARgg0QIdgAEYINECHYABGCDRAh2AARgg0QIdgAEYINECHYABGC
DRAh2AARgg0QIdgAEYINECHYABGCDRAh2AARgg0QIdgAEYINECHYABGCDRAh2AARgg0QIdgAEYIN
ECHYABEnn9/5YvWGmZn57cU/qyfMD9ufVk+Yvw6PV0+Y/as/V0+YlxdPVk+Yw2G/esIcji9XT+AS
8WEDRAg2QIRgA0QINkCEYANECDZAhGADRAg2QIRgA0QINkCEYANECDZAhGADRAg2QIRgA0QINkCE
YANECDZAhGADRAg2QIRgA0QINkCEYANECDZAhGADRAg2QIRgA0QINkCEYANECDZAhGADRAg2QMTm
288+Pa4eMTNzujtfPWEOx/X3a7+/vnrC/PH3zdUT5tent1dPmLNnp6snzNmzK6snzC/7i9UT5sfD
76snzNnhu9UTfNgAFYINECHYABGCDRAh2AARgg0QIdgAEYINECHYABGCDRAh2AARgg0QIdgAEYIN
ECHYABGCDRAh2AARgg0QIdgAEYINECHYABGCDRAh2AARgg0QIdgAEYINECHYABGCDRAh2AARgg0Q
IdgAEYINEHHy6uJyNPudDx+tnjBXP7m5esK8eO/h6gkzdz9evWCun95bPWGe739ePWHm8derF8xr
33+zesK8+urp6gnz6MuPVk/wYQNUCDZAhGADRAg2QIRgA0QINkCEYANECDZAhGADRAg2QIRgA0QI
NkCEYANECDZAhGADRAg2QIRgA0QINkCEYANECDZAhGADRAg2QIRgA0QINkCEYANECDZAhGADRAg2
QIRgA0QINkCEYANECDZAxOb27oPj6hEzM/e376+eMA+2b66eMPd2V1ZPmPs3LlZPmPs3zldPmLdv
Plk9Yd54ff2G3e756gmz3RxWT5jz/W71BB82QIVgA0QINkCEYANECDZAhGADRAg2QIRgA0QINkCE
YANECDZAhGADRAg2QIRgA0QINkCEYANECDZAhGADRAg2QIRgA0QINkCEYANECDZAhGADRAg2QIRg
A0QINkCEYANECDZAhGADRAg2QIRgA0RsZk6Oq0dwuWw3V1dPmO12t3rCXL1ya/WE2Z3cWT1hbm3v
rp4w7x4erJ4wb127tnqCDxugQrABIgQbIEKwASIEGyBCsAEiBBsgQrABIgQbIEKwASIEGyBCsAEi
BBsgQrABIgQbIEKwASIEGyBCsAEiBBsgQrABIgQbIEKwASIEGyBCsAEiBBsgQrABIgQbIEKwASIE
GyBCsAEiBBsgQrABIjYzJ8fVIwD4bz5sgAjBBogQbIAIwQaIEGyACMEGiBBsgAjBBogQbIAIwQaI
EGyACMEGiBBsgAjBBogQbIAIwQaIEGyACMEGiBBsgAjBBogQbIAIwQaIEGyACMEGiBBsgAjBBogQ
bIAIwQaIEGyACMEGiBBsgAjBBogQbIAIwQaIEGyACMEGiBBsgAjBBogQbIAIwQaIEGyACMEGiBBs
gAjBBogQbIAIwQaIEGyACMEGiBBsgAjBBogQbIAIwQaIEGyACMEGiBBsgAjBBogQbIAIwQaIEGyA
CMEGiBBsgAjBBogQbIAIwQaIEGyACMEGiBBsgAjBBogQbIAIwQaIEGyACMEGiBBsgAjBBogQbIAI
wQaIEGyACMEGiBBsgAjBBogQbIAIwQaIEGyACMEGiBBsgAjBBogQbIAIwQaIEGyACMEGiBBsgAjB
BogQbIAIwQaIEGyACMEGiBBsgAjBBoj4Fzm6TT6iMV/eAAAAAElFTkSuQmCC
" transform="translate(96, 12)"/>
 
 
 
 
 
 
 
<image width="18" height="364" xlink:href="data:;base64,
iVBORw0KGgoAAAANSUhEUgAAABIAAAFsCAYAAADBkelSAAACHUlEQVR4nO2c223EMAwEqUD9V5Eu
4yOvBPpjEAwIqoCF9kU5vljnyd8KYP0QIBERN+thgAoC4qhVzqVmcw0Te7BGHLWgkk0BgdQo1yZr
lH8Q0Ca7Wxy1Ux8GKBICOhAQaT+lESQ2aD9Gbe1vgU4mAiSkRgEpk824NjnZRvsh1yj7la6N1Qi0
35ZsnWtC+yORF1pxo3zUMNcYjZTUVqMeCMFBqUFAUGeN1HRA5Ds2CKjyIEBK+xlqt8qnEUSNAiLf
+Y+lFslgTdaImkc3itmUkJpxZm+ym3XLppHwOKI0Eh5HXPt1gw2035Zs0P6x7QeT7aO2rrVAtooY
2++z33aukf8PKSutUKNN9j8C5WrUraXWL18gZ2s09mlk8DzaZPdAQvtDRk1oP/TjupMaZT+Uo8Gl
NdpPAQmpYa7pks2VFhtsOo249iMwS+3NMs5sBEbZ/qXWA/ke2AfPbIya8WEUAtJVZO3vF2g/g6Oc
2XM1AqnZkg0eRxAQtSOlRmt/s4TUVqMXQAyOcmbr5pFu1N6CPqoRJntwaXU5MrZfl+zB1MCfM6Dv
sn3n2s7sF0A6apTYGDWhRkmVVpjswa5R1Ar6etmo0cGo2a4JoXYE2n909nPJttkPltZ2/xGYbOge
LZ/9Oo2WWr/A0kI34GA7Iv/KnksNm0eDNeKo6dq/rvVAVEWoHQmHf+kumcaoBfQmArwngnON0sjX
fs7+udQgoC/rNOfnsknqIwAAAABJRU5ErkJggg==
" transform="translate(472, 12)"/>
 
 
 500 
 
 
 1000 
 
 
 1500 
 
 
 2000 
 
 
 2500 
 
 
 3000

min value = 5.0
max value = 3218.380280997004
Policy for the 2 link acrobot  in unstable equilibrium:


<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 -10 
 
 
 -5 
 
 
 0 
 
 
 5 
 
 
 10 
 
 
 -10 
 
 
 -5 
 
 
 0 
 
 
 5 
 
 
 10 
 
 
<image width="364" height="364" xlink:href="data:;base64,
iVBORw0KGgoAAAANSUhEUgAAAWwAAAFsCAYAAADon4O5AAAFsUlEQVR4nO3WsU2VYRiG4f8YEhsd
gsIVhAUYgTHchREosDbUpyCxMzRswBKUh/w2GmNCot373cl1TfBUd57D8eJ63wBY3rvpAQD8H8EG
iBBsgAjBBogQbIAIwQaIEGyACMEGiBBsgAjBBogQbIAIwQaIEGyACMEGiBBsgAjBBogQbIAIwQaI
EGyACMEGiBBsgAjBBogQbIAIwQaIEGyACMEGiBBsgAjBBogQbIAIwQaIEGyACMEGiBBsgAjBBogQ
bIAIwQaIEGyACMEGiBBsgAjBBogQbIAIwQaIEGyACMEGiBBsgAjBBogQbIAIwQaIEGyACMEGiBBs
gAjBBogQbIAIwQaIEGyACMEGiBBsgAjBBogQbIAIwQaIEGyACMEGiBBsgAjBBogQbIAIwQaIEGyA
CMEGiBBsgAjBBogQbIAIwQaIEGyACMEGiBBsgAjBBogQbIAIwQaIEGyACMEGiBBsgAjBBogQbIAI
wQaIEGyACMEGiBBsgAjBBogQbIAIwQaIEGyACMEGiBBsgAjBBogQbIAIwQaIEGyACMEGiBBsgIiz
6QG/Xf34Nj1hCaf9dnoCC3m4vJ+ewEI8bIAIwQaIEGyACMEGiBBsgAjBBogQbIAIwQaIEGyACMEG
iBBsgAjBBogQbIAIwQaIEGyACMEGiBBsgAjBBogQbIAIwQaIEGyACMEGiBBsgAjBBogQbIAIwQaI
EGyACMEGiBBsgAjBBogQbIAIwQaIOJz2u316BPC2Tx+/Tk/Ynl+O0xP4xcMGiBBsgAjBBogQbIAI
wQaIEGyACMEGiBBsgAjBBogQbIAIwQaIEGyACMEGiBBsgAjBBogQbIAIwQaIEGyACMEGiBBsgAjB
BogQbIAIwQaIEGyACMEGiBBsgAjBBogQbIAIwQaIEGyACMEGiBBsgIiz6QEreX28mZ6whO9fzqcn
sJDzD1fTE7bnl+P0hCV42AARgg0QIdgAEYINECHYABGCDRAh2AARgg0QIdgAEYINECHYABGCDRAh
2AARgg0QIdgAEYINECHYABGCDRAh2AARgg0QIdgAEYINECHYABGCDRAh2AARgg0QIdgAEYINECHY
ABGCDRAh2AARgg0QcTjtd/v0CP54fbyZnrC9//w0PQF4g4cNECHYABGCDRAh2AARgg0QIdgAEYIN
ECHYABGCDRAh2AARgg0QIdgAEYINECHYABGCDRAh2AARgg0QIdgAEYINECHYABGCDRAh2AARgg0Q
IdgAEYINECHYABGCDRAh2AARgg0QIdgAEYINECHYABFnD5f30xv4y/n0gG3bnqYHsJDTfjs9YQkr
tNLDBogQbIAIwQaIEGyACMEGiBBsgAjBBogQbIAIwQaIEGyACMEGiBBsgAjBBogQbIAIwQaIEGyA
CMEGiBBsgAjBBogQbIAIwQaIEGyACMEGiBBsgAjBBogQbIAIwQaIEGyACMEGiBBsgAjBBogQbICI
w/Hiep8eAcC/edgAEYINECHYABGCDRAh2AARgg0QIdgAEYINECHYABGCDRAh2AARgg0QIdgAEYIN
ECHYABGCDRAh2AARgg0QIdgAEYINECHYABGCDRAh2AARgg0QIdgAEYINECHYABGCDRAh2AARgg0Q
IdgAEYINECHYABGCDRAh2AARgg0QIdgAEYINECHYABGCDRAh2AARgg0QIdgAEYINECHYABGCDRAh
2AARgg0QIdgAEYINECHYABGCDRAh2AARgg0QIdgAEYINECHYABGCDRAh2AARgg0QIdgAEYINECHY
ABGCDRAh2AARgg0QIdgAEYINECHYABGCDRAh2AARgg0QIdgAEYINECHYABGCDRAh2AARgg0QIdgA
EYINECHYABGCDRAh2AARgg0QIdgAEYINECHYABGCDRAh2AARgg0QIdgAEYINECHYABGCDRAh2AAR
gg0QIdgAEYINEPET6Fko8fl4nSEAAAAASUVORK5CYII=
" transform="translate(96, 12)"/>
 
 
 
 
 
 
 
<image width="18" height="364" xlink:href="data:;base64,
iVBORw0KGgoAAAANSUhEUgAAABIAAAFsCAYAAADBkelSAAACHUlEQVR4nO2c223EMAwEqUD9V5Eu
4yOvBPpjEAwIqoCF9kU5vljnyd8KYP0QIBERN+thgAoC4qhVzqVmcw0Te7BGHLWgkk0BgdQo1yZr
lH8Q0Ca7Wxy1Ux8GKBICOhAQaT+lESQ2aD9Gbe1vgU4mAiSkRgEpk824NjnZRvsh1yj7la6N1Qi0
35ZsnWtC+yORF1pxo3zUMNcYjZTUVqMeCMFBqUFAUGeN1HRA5Ds2CKjyIEBK+xlqt8qnEUSNAiLf
+Y+lFslgTdaImkc3itmUkJpxZm+ym3XLppHwOKI0Eh5HXPt1gw2035Zs0P6x7QeT7aO2rrVAtooY
2++z33aukf8PKSutUKNN9j8C5WrUraXWL18gZ2s09mlk8DzaZPdAQvtDRk1oP/TjupMaZT+Uo8Gl
NdpPAQmpYa7pks2VFhtsOo249iMwS+3NMs5sBEbZ/qXWA/ke2AfPbIya8WEUAtJVZO3vF2g/g6Oc
2XM1AqnZkg0eRxAQtSOlRmt/s4TUVqMXQAyOcmbr5pFu1N6CPqoRJntwaXU5MrZfl+zB1MCfM6Dv
sn3n2s7sF0A6apTYGDWhRkmVVpjswa5R1Ar6etmo0cGo2a4JoXYE2n909nPJttkPltZ2/xGYbOge
LZ/9Oo2WWr/A0kI34GA7Iv/KnksNm0eDNeKo6dq/rvVAVEWoHQmHf+kumcaoBfQmArwngnON0sjX
fs7+udQgoC/rNOfnsknqIwAAAABJRU5ErkJggg==
" transform="translate(472, 12)"/>
 
 
 - 
 
 
 10.0 
 
 
 - 
 
 
 7.5 
 
 
 - 
 
 
 5.0 
 
 
 - 
 
 
 2.5 
 
 
 0 
 
 
 2.5 
 
 
 5.0 
 
 
 7.5 
 
 
 10.0 
 
<polyline clip-path="url(#clip6700)" style="stroke:#000000; stroke-width:1; stroke-opacity:1; fill:none" points="
 490.083,375.813 490.083,359.268 496.083,359.268 490.083,359.268 490.083,317.904 496.083,317.904 490.083,317.904 490.083,276.54 496.083,276.54 490.083,276.54 
 490.083,235.176 496.083,235.176 490.083,235.176 490.083,193.812 496.083,193.812 490.083,193.812 490.083,152.448 496.083,152.448 490.083,152.448 490.083,111.084 
 496.083,111.084 490.083,111.084 490.083,69.7205 496.083,69.7205 490.083,69.7205 490.083,28.3566 496.083,28.3566 490.083,28.3566 490.083,11.811 
 "/>

min torque = -11.0
max torque = 11.0


In [271]:
anim(init_vertical_perturbed(Val{2}), sim3, get_optimal_policy(vi3), advance, "discrete_vi_acrobot_simple11", 2000)

It seems that increasing resolution is not sufficient, or that we need to further increase it to get a proper balancing behaviour. Alternatively we can try tweaking the reward function and our interpolation scheme to improve the results.

Furthermore it is worth noting that a large portion of the policy with $\theta_1$ close to $0$ produces almost no torque, which means this policy will be unable to swing the pendulum away from its stable equillibrium. This is possibly the result of severely penalizing low angles for $\theta_1$.

# Conclusions

In conclusion we have attempted, with variable success, to balance an Acrobot using a forward simulator as our reference. Although each method has its trade-offs it seems that the only method able to reliably achieve balancing is the optimization with lookahead. Perhaps a combination of these methods can be used to apply in a more complex setting: for instance value iteration can be used to learn a reasonable swing-up technique, while the final balancing stage can be accomplished with optimization.

## Future Work

This project, in my opinion leaves much to be desired from the methods implemented. There is still a lot of room left for exploring more effective methods for balancing the Acrobot. Perhaps two separate policies can be learned: one for balancing and one for swinging. Combining the two could produce a complete method for swinging and balancing the Acrobot that is independent of initial state.

## Notes on the implementation

There are some things to be said about using Julia and Jupyter notebooks for a project like this. Although the syntax closely resembles MATLAB, making it familiar to others versed in scientific computing, it deviates from this norm when performance is important. My first implementation of this project used mutable state at global scope and standard unencapsulated arrays. Rewriting the entirety of the methods within this notebook improved performance by orders of magnitude (it took a half hour to run a value iteration instance instead of a day). This somewhat limits the types of programs with readable syntax, because performant code needs to be verbose to provide the compile with more information for optimization. The big promise of Julia is to allow one to write a prototype and be able to optimize it for production use in the same language. Perhaps this is overstated, but it is certainly useful to be able to write small prototypes within a larger code base.
Because Jupyter notebooks are missing many features other IDEs may offer, it can be annoying to edit large amounts of code.

With that said, it took me next to no time to parallelize the existing code making it noticeably faster using Julia's `@sync`, `@parallel` and `@everywhere` macros. Furthermore the available libraries for scientific computing applications are very numerous and easy to use. Most notably, I found `Optim.jl`, `Plots.jl` and `JLD.jl` especially useful for this project.